## __Check first before starting__

In [1]:
import os

# Change the working directory to the project root
# Working_directory = os.path.normpath("C:/Users/james/OneDrive/文件/Continual_Learning")
Working_directory = os.path.normpath("/mnt/mydisk/Continual_Learning_JL/Continual_Learning/")
os.chdir(Working_directory)
print(f"Working directory: {os.getcwd()}")

Working directory: /mnt/mydisk/Continual_Learning_JL/Continual_Learning


## __All imports__

In [2]:
# Operating system and file management
import os
import shutil
import contextlib
import traceback
import gc
import glob, copy
from collections import defaultdict
import subprocess
import time
import re, pickle

# Jupyter notebook widgets and display
import ipywidgets as widgets
from IPython.display import display

# Data manipulation and analysis
import pandas as pd
import numpy as np

# Plotting and visualization
import matplotlib.pyplot as plt
from mpl_interactions import zoom_factory, panhandler

# Machine learning and preprocessing
from sklearn.preprocessing import LabelEncoder
from sklearn.model_selection import train_test_split
import pickle
from ta import trend, momentum, volatility, volume

# Mathematical and scientific computing
import math
from scipy.ndimage import gaussian_filter1d

# Type hinting
from typing import Callable, Tuple

# Deep learning with PyTorch
import torch
import torch.nn as nn
import torch.optim as optim
import torch.nn.functional as F
from torch.utils.data import DataLoader, TensorDataset

## __Dataset Setup & Preprocessing__

### 📥 Step 1 — Set dataset path and load features & labels
We will load the 561-dimensional features and original activity labels for both training and testing.

In [3]:
# Set working directory manually before running this cell if needed
BASE_DIR = "Class_Incremental_CL/HAR_CIL/har_dataset"
TRAIN_DIR = os.path.join(BASE_DIR, "train")
TEST_DIR = os.path.join(BASE_DIR, "test")

# 活動對應（原始標籤）
activity_label_map = {
    1: "WALKING",
    2: "WALKING_UPSTAIRS",
    3: "WALKING_DOWNSTAIRS",
    4: "SITTING",
    5: "STANDING",
    6: "LAYING"
}

# Load feature and label data
X_train = np.loadtxt(os.path.join(TRAIN_DIR, "X_train.txt"))
y_train = np.loadtxt(os.path.join(TRAIN_DIR, "y_train.txt")).astype(int)
X_test = np.loadtxt(os.path.join(TEST_DIR, "X_test.txt"))
y_test = np.loadtxt(os.path.join(TEST_DIR, "y_test.txt")).astype(int)

print("Train shape:", X_train.shape, y_train.shape)
print("Test shape:", X_test.shape, y_test.shape)

Train shape: (7352, 561) (7352,)
Test shape: (2947, 561) (2947,)


### 🧩 Step 2 — Define period label groups and final class remapping
We will predefine the class mappings for each period to ensure consistency across the experiment.

In [4]:
# Period-to-original-label mapping
period_label_map = {
    1: [4, 5],           # SITTING, STANDING
    2: [4, 5, 1, 2, 3],  # + WALKING variants (merged)
    3: [4, 5, 1, 2, 3, 6],  # + LAYING
    4: [4, 5, 1, 2, 3, 6]   # same classes, but with walking variants separated
}

# Consistent label remapping across all periods (final label index)
final_class_map = {
    "SITTING": 0,
    "STANDING": 1,
    "WALKING": 2,
    "LAYING": 3,
    "WALKING_UPSTAIRS": 4,
    "WALKING_DOWNSTAIRS": 5
}

# Reverse mapping for readability
label_name_from_id = {v: k for k, v in final_class_map.items()}
activity_label_map = {
    1: "WALKING",
    2: "WALKING_UPSTAIRS",
    3: "WALKING_DOWNSTAIRS",
    4: "SITTING",
    5: "STANDING",
    6: "LAYING"
}


### 🧪 Step 3 — Filter and remap datasets for each period
We will build training and testing splits for each period using consistent class indices.

In [5]:
def map_label(label, period):
    name = activity_label_map[label]
    if period < 4:
        if name.startswith("WALKING"):
            return final_class_map["WALKING"]
        else:
            return final_class_map[name]
    else:
        return final_class_map[name]

def get_period_dataset(X, y, period):
    allowed_labels = period_label_map[period]
    mask = np.isin(y, allowed_labels)
    Xp = X[mask]
    yp = np.array([map_label(label, period) for label in y[mask]])
    return Xp, yp


### 📊 Step 4 — Print artistic class distribution for each period
We show each period's label map and class statistics to confirm correctness.

In [6]:
def print_class_distribution(y, var_name: str, label_map: dict) -> None:
    y = np.array(y).flatten()
    unique, counts = np.unique(y, return_counts=True)
    total = counts.sum()
    print(f"\n📦 Class Distribution for {var_name}")
    for i, c in zip(unique, counts):
        print(f"  ├─ Label {i:<2} ({label_map[i]:<20}) → {c:>5} samples ({(c/total)*100:>5.2f}%)")


In [7]:
period_datasets = {}

for period in range(1, 5):
    Xp_train, yp_train = get_period_dataset(X_train, y_train, period)
    Xp_test, yp_test = get_period_dataset(X_test, y_test, period)

    period_datasets[period] = {
        "train": (Xp_train, yp_train),
        "test": (Xp_test, yp_test)
    }

    print_class_distribution(yp_train, f"Period {period} (Train)", label_name_from_id)
    print_class_distribution(yp_test, f"Period {period} (Test)", label_name_from_id)



📦 Class Distribution for Period 1 (Train)
  ├─ Label 0  (SITTING             ) →  1286 samples (48.35%)
  ├─ Label 1  (STANDING            ) →  1374 samples (51.65%)

📦 Class Distribution for Period 1 (Test)
  ├─ Label 0  (SITTING             ) →   491 samples (48.00%)
  ├─ Label 1  (STANDING            ) →   532 samples (52.00%)

📦 Class Distribution for Period 2 (Train)
  ├─ Label 0  (SITTING             ) →  1286 samples (21.63%)
  ├─ Label 1  (STANDING            ) →  1374 samples (23.11%)
  ├─ Label 2  (WALKING             ) →  3285 samples (55.26%)

📦 Class Distribution for Period 2 (Test)
  ├─ Label 0  (SITTING             ) →   491 samples (20.37%)
  ├─ Label 1  (STANDING            ) →   532 samples (22.07%)
  ├─ Label 2  (WALKING             ) →  1387 samples (57.55%)

📦 Class Distribution for Period 3 (Train)
  ├─ Label 0  (SITTING             ) →  1286 samples (17.49%)
  ├─ Label 1  (STANDING            ) →  1374 samples (18.69%)
  ├─ Label 2  (WALKING             ) →  328

## __Check GPU, CUDA, Pytorch__

### GPU Details

In [8]:
!nvidia-smi

Sat Apr 26 22:29:22 2025       
+-----------------------------------------------------------------------------------------+
| NVIDIA-SMI 570.86.15              Driver Version: 570.86.15      CUDA Version: 12.8     |
|-----------------------------------------+------------------------+----------------------+
| GPU  Name                 Persistence-M | Bus-Id          Disp.A | Volatile Uncorr. ECC |
| Fan  Temp   Perf          Pwr:Usage/Cap |           Memory-Usage | GPU-Util  Compute M. |
|                                         |                        |               MIG M. |
|=========================================+========================+======================|
|   0  NVIDIA RTX A6000               Off |   00000000:2A:00.0 Off |                  Off |
| 30%   54C    P2            128W /  300W |   20898MiB /  49140MiB |     24%      Default |
|                                         |                        |                  N/A |
+-----------------------------------------+-----

### CUDA Details

In [9]:
def check_gpu_config():
    """
    Check GPU availability and display detailed configuration information.
    """
    # Check if GPU is available
    gpu_available = torch.cuda.is_available()
    
    # Print header
    print("=" * 50)
    print("GPU Configuration Check".center(50))
    print("=" * 50)
    
    # Basic GPU availability
    print(f"{'PyTorch Version':<25}: {torch.__version__}")
    print(f"{'GPU Available':<25}: {'Yes' if gpu_available else 'No'}")
    
    # If GPU is available, print detailed info
    if gpu_available:
        print("-" * 50)
        print("GPU Details".center(50))
        print("-" * 50)
        
        # Device info
        print(f"{'Device Name':<25}: {torch.cuda.get_device_name(0)}")
        print(f"{'Number of GPUs':<25}: {torch.cuda.device_count()}")
        print(f"{'Current Device Index':<25}: {torch.cuda.current_device()}")
        
        # Compute capability and CUDA cores
        props = torch.cuda.get_device_properties(0)
        print(f"{'Compute Capability':<25}: {props.major}.{props.minor}")
        print(f"{'Total CUDA Cores':<25}: {props.multi_processor_count * 128}")  # Approx. 128 cores per SM
        
        # Memory info
        total_memory = props.total_memory / (1024 ** 3)  # Convert to GB
        memory_allocated = torch.cuda.memory_allocated(0) / (1024 ** 3)
        memory_reserved = torch.cuda.memory_reserved(0) / (1024 ** 3)
        print(f"{'Total Memory (GB)':<25}: {total_memory:.2f}")
        print(f"{'Allocated Memory (GB)':<25}: {memory_allocated:.2f}")
        print(f"{'Reserved Memory (GB)':<25}: {memory_reserved:.2f}")
    else:
        print("-" * 50)
        print("No GPU detected. Running on CPU.".center(50))
        print("-" * 50)
    
    print("=" * 50)

if __name__ == "__main__":
    check_gpu_config()

             GPU Configuration Check              
PyTorch Version          : 2.5.1
GPU Available            : Yes
--------------------------------------------------
                   GPU Details                    
--------------------------------------------------
Device Name              : NVIDIA RTX A6000
Number of GPUs           : 3
Current Device Index     : 0
Compute Capability       : 8.6
Total CUDA Cores         : 10752
Total Memory (GB)        : 47.41
Allocated Memory (GB)    : 0.00
Reserved Memory (GB)     : 0.00


### PyTorch Details

In [10]:
def print_torch_config():
    """Print PyTorch and CUDA configuration in a formatted manner."""
    print("=" * 50)
    print("PyTorch Configuration".center(50))
    print("=" * 50)
    
    # Basic PyTorch and CUDA info
    print(f"{'PyTorch Version':<25}: {torch.__version__}")
    print(f"{'CUDA Compiled Version':<25}: {torch.version.cuda}")
    print(f"{'CUDA Available':<25}: {'Yes' if torch.cuda.is_available() else 'No'}")
    print(f"{'Number of GPUs':<25}: {torch.cuda.device_count()}")

    # GPU details if available
    if torch.cuda.is_available():
        print(f"{'GPU Name':<25}: {torch.cuda.get_device_name(0)}")

    print("-" * 50)
    
    # Seed setting
    torch.manual_seed(42)
    print(f"{'Random Seed':<25}: 42 (Seeding successful!)")
    
    print("=" * 50)

if __name__ == "__main__":
    print_torch_config()

              PyTorch Configuration               
PyTorch Version          : 2.5.1
CUDA Compiled Version    : 12.1
CUDA Available           : Yes
Number of GPUs           : 3
GPU Name                 : NVIDIA RTX A6000
--------------------------------------------------
Random Seed              : 42 (Seeding successful!)


## __⚙️ GPU Selection — Auto-select the least loaded GPU__
This code automatically scans available GPUs and selects the one with the lowest current memory usage.


In [11]:
def auto_select_cuda_device(verbose=True):
    """
    Automatically selects the CUDA GPU with the least memory usage.
    Falls back to CPU if no GPU is available.
    """
    if not torch.cuda.is_available():
        print("🚫 No CUDA GPU available. Using CPU.")
        return torch.device("cpu")

    try:
        # Run nvidia-smi to get memory usage of each GPU
        smi_output = subprocess.check_output(
            ['nvidia-smi', '--query-gpu=memory.used', '--format=csv,nounits,noheader'],
            encoding='utf-8'
        )
        memory_used = [int(x) for x in smi_output.strip().split('\n')]
        best_gpu = int(np.argmin(memory_used))

        if verbose:
            print("🎯 Automatically selected GPU:")
            print(f"    - CUDA Device ID : {best_gpu}")
            print(f"    - Memory Used    : {memory_used[best_gpu]} MiB")
            print(f"    - Device Name    : {torch.cuda.get_device_name(best_gpu)}")
        return torch.device(f"cuda:{best_gpu}")
    except Exception as e:
        print(f"⚠️ Failed to auto-detect GPU. Falling back to cuda:0. ({e})")
        return torch.device("cuda:0" if torch.cuda.is_available() else "cpu")

# Execute and assign
device = auto_select_cuda_device()

🎯 Automatically selected GPU:
    - CUDA Device ID : 0
    - Memory Used    : 20898 MiB
    - Device Name    : NVIDIA RTX A6000


## __MLP Model with LoRA__

### HAR_MLP_LoRA_v2

In [12]:
class LoRA(nn.Module):
    def __init__(self, linear_layer: nn.Linear, rank: int):
        super(LoRA, self).__init__()
        self.linear = linear_layer
        self.rank = rank

        in_features, out_features = linear_layer.weight.shape
        self.A = nn.Parameter(torch.zeros(in_features, rank))
        self.B = nn.Parameter(torch.zeros(rank, out_features))

        nn.init.normal_(self.A, mean=0, std=1)
        nn.init.zeros_(self.B)

    def forward(self, x: torch.Tensor) -> torch.Tensor:
        lora_delta = self.A @ self.B
        adapted_weight = self.linear.weight + lora_delta
        return F.linear(x, adapted_weight, self.linear.bias)

    def parameters(self, recurse=True):
        return [self.A, self.B]

class HAR_MLP_LoRA_v2(nn.Module):
    def __init__(self, input_size: int, hidden_size: int, output_size: int, dropout: float = 0.2, lora_rank: int = 8):
        super(HAR_MLP_LoRA_v2, self).__init__()
        self.fc1 = nn.Linear(input_size, hidden_size)
        self.bn1 = nn.BatchNorm1d(hidden_size)
        self.relu1 = nn.ReLU()
        self.dropout1 = nn.Dropout(dropout)

        self.fc2 = nn.Linear(hidden_size, hidden_size)
        self.lora_adapters = nn.ModuleList()
        self.lora_rank = lora_rank
        self.bn2 = nn.BatchNorm1d(hidden_size)
        self.relu2 = nn.ReLU()
        self.dropout2 = nn.Dropout(dropout)

        self.fc3 = nn.Linear(hidden_size, output_size)
        self.init_weights()

    def init_weights(self):
        for m in self.modules():
            if isinstance(m, nn.Linear):
                nn.init.xavier_uniform_(m.weight)
                nn.init.constant_(m.bias, 0)

    def add_lora_adapter(self):
        new_lora = LoRA(self.fc2, self.lora_rank)
        device = next(self.parameters()).device
        new_lora.to(device)
        self.lora_adapters.append(new_lora)
        print(f"✅ Added LoRA adapter to HAR_MLP_LoRA_v2 (fc2), total adapters: {len(self.lora_adapters)}")

    def forward(self, x):
        x = self.fc1(x)
        x = self.bn1(x)
        x = self.relu1(x)
        x = self.dropout1(x)

        x_base = self.fc2(x)
        if self.lora_adapters:
            lora_delta = sum(lora.A @ lora.B for lora in self.lora_adapters)
            adapted_weight = self.fc2.weight + lora_delta
            x = F.linear(x, adapted_weight, self.fc2.bias)
        else:
            x = x_base

        x = self.bn2(x)
        x = self.relu2(x)
        x = self.dropout2(x)
        x = self.fc3(x)
        return x

## __Training Function with DynEx-CLoRA__

In [13]:
def compute_classwise_accuracy(preds, targets, class_correct, class_total):
    """
    Computes per-class accuracy statistics from raw logits and ground truth.
    """
    preds = torch.argmax(preds, dim=-1)
    correct_mask = (preds == targets)
    for label in torch.unique(targets):
        label = label.item()
        label_mask = (targets == label)
        class_total[label] = class_total.get(label, 0) + label_mask.sum().item()
        class_correct[label] = class_correct.get(label, 0) + (correct_mask & label_mask).sum().item()

In [14]:
# HAR version of DynEx-CLoRA training function supporting all Periods
# Unified for both LoRA and DynEx-CLoRA (logic controlled by `logic_version`)
def train_with_dynex_clora(model, teacher_model, output_size, criterion, optimizer,
                           X_train, y_train, X_val, y_val,
                           num_epochs, batch_size, alpha,
                           model_saving_folder, model_name,
                           stop_signal_file=None, scheduler=None,
                           period=None, stable_classes=None,
                           logic_version="average",  # "average" or "all"
                           similarity_threshold=0.0,
                           class_features_dict=None, related_labels=None):

    print(f"\n🚀 'train_with_dynex_clora' started for Period {period}\n")

    model_name = model_name or 'dynex_clora_model'
    model_saving_folder = model_saving_folder or './saved_models'
    if os.path.exists(model_saving_folder):
        shutil.rmtree(model_saving_folder)
        print(f"✅ Removed existing folder: {model_saving_folder}")
    os.makedirs(model_saving_folder, exist_ok=True)

    device = auto_select_cuda_device()
    model.to(device)
    if teacher_model:
        teacher_model.to(device)
        teacher_model.eval()

    X_train = torch.tensor(X_train, dtype=torch.float32).to(device)
    y_train = torch.tensor(y_train, dtype=torch.long).to(device)
    X_val = torch.tensor(X_val, dtype=torch.float32).to(device)
    y_val = torch.tensor(y_val, dtype=torch.long).to(device)

    train_loader = DataLoader(TensorDataset(X_train, y_train), batch_size=batch_size, shuffle=True)
    val_loader = DataLoader(TensorDataset(X_val, y_val), batch_size=batch_size, shuffle=False)

    print("\n✅ Data Overview:")
    print(f"X_train: {X_train.shape}, y_train: {y_train.shape}")
    print(f"X_val: {X_val.shape}, y_val: {y_val.shape}")

    start_time = time.time()
    best_results = []

    # === Class Feature Extraction ===
    model.eval()
    new_class_features = {}
    with torch.no_grad():
        for xb, yb in train_loader:
            x = model.relu1(model.bn1(model.fc1(xb)))
            for cls in torch.unique(yb):
                cls_mask = (yb == cls)
                cls_feat = x[cls_mask]
                if cls.item() not in new_class_features:
                    new_class_features[cls.item()] = []
                new_class_features[cls.item()].append(cls_feat)
    for cls in new_class_features:
        new_class_features[cls] = torch.cat(new_class_features[cls], dim=0).mean(dim=0)

    # === Similarity Computation (only for Period > 1) ===
    if period > 1 and class_features_dict:
        cosine_sim = torch.nn.CosineSimilarity(dim=0)
        similarity_scores = {}

        for new_label, new_feat in new_class_features.items():
            similarity_scores[new_label] = {}
            for old_label, old_feat in class_features_dict.items():
                sim = cosine_sim(new_feat.to(device), old_feat.to(device)).item()
                similarity_scores[new_label][old_label] = sim

        print("\n🔎 Similarity Scores:")
        for new_label, scores in similarity_scores.items():
            print(f"New Class {new_label}:")
            if scores:
                for old_label, score in scores.items():
                    print(f"  - Existing Class {old_label}: {score:.4f}")
            else:
                print("  - No existing classes to compare")

        all_similarities = [s for scores in similarity_scores.values() for s in scores.values()]
        if all_similarities:
            avg_similarity = np.mean(all_similarities)
            std_similarity = np.std(all_similarities)
            print(f"📊 Average similarity: {avg_similarity:.4f}, Std: {std_similarity:.4f}")

        print(f"🧩 Similarity threshold: {similarity_threshold}")
        print(f"👥 Existing classes: {list(class_features_dict.keys())}")
        print(f"🆕 New classes: {list(new_class_features.keys())}")

    to_unfreeze = set()

    # === Period-specific freeze/unfreeze logic ===
    if period == 1:
        for p in model.fc1.parameters():
            p.requires_grad = True
        for p in model.fc2.parameters():
            p.requires_grad = True
        for p in model.fc3.parameters():
            p.requires_grad = True
        for adapter in model.lora_adapters:
            for p in adapter.parameters():
                p.requires_grad = True

    elif period > 1 and class_features_dict:
        new_lora_indices = []
        cosine_sim = torch.nn.CosineSimilarity(dim=0)

        existing_classes = set(class_features_dict.keys())
        current_classes = set(new_class_features.keys())
        new_classes = current_classes - existing_classes
        print(f"🧩 New classes detected (for LoRA decision): {sorted(new_classes)}")

        # --- 新類別邏輯 ---
        for new_cls in new_classes:
            new_feat = new_class_features[new_cls]
            sims = [cosine_sim(new_feat.to(device), class_features_dict[old_cls].to(device)).item()
                    for old_cls in class_features_dict]
            
            if logic_version == "average":
                avg_sim = np.mean(sims)
                print(f"[Similarity] Class {new_cls} - Avg Sim = {avg_sim:.4f}")
                if avg_sim < similarity_threshold:
                    model.add_lora_adapter()
                    new_idx = len(model.lora_adapters) - 1
                    related_labels[new_idx] = [new_cls]
                    new_lora_indices.append(new_idx)
                # 類似的舊類別 → 解凍
                for i, old_cls in enumerate(class_features_dict):
                    if sims[i] >= similarity_threshold:
                        for k, v in related_labels.items():
                            if old_cls in v:
                                to_unfreeze.add(k)
                                if new_cls not in related_labels[k]:
                                    related_labels[k].append(new_cls)
                                    print(f"🔄 New Class {new_cls} is similar to Old Class {old_cls} (Sim={sims[i]:.4f}) → " f"Associated with network '{k}', related_labels[{k}] now: {related_labels[k]}")
                                else:
                                    print(f"🔁 New Class {new_cls} already associated with '{k}' due to similarity with Old Class {old_cls} (Sim={sims[i]:.4f})")

            elif logic_version == "all":
                matched = False
                for i, old_cls in enumerate(class_features_dict):
                    if sims[i] >= similarity_threshold:
                        matched = True
                        for k, v in related_labels.items():
                            if old_cls in v:
                                to_unfreeze.add(k)
                                if new_cls not in related_labels[k]:
                                    related_labels[k].append(new_cls)
                                    print(f"🔄 New Class {new_cls} is similar to Old Class {old_cls} (Sim={sims[i]:.4f}) → " f"Associated with network '{k}', related_labels[{k}] now: {related_labels[k]}")
                                else:
                                    print(f"🔁 New Class {new_cls} already associated with '{k}' due to similarity with Old Class {old_cls} (Sim={sims[i]:.4f})")
                
                if not matched:
                    model.add_lora_adapter()
                    new_idx = len(model.lora_adapters) - 1
                    related_labels[new_idx] = [new_cls]
                    new_lora_indices.append(new_idx)

        # --- 舊類別穩定性檢查（自己 vs 自己的舊版本）(在看需不需要) ---
        for old_cls in existing_classes:
            if old_cls in new_class_features:
                sim_self = cosine_sim(new_class_features[old_cls].to(device), class_features_dict[old_cls].to(device)).item()
                print(f"[Stability Check] Class {old_cls} similarity with itself: {sim_self:.4f}")
                if sim_self < similarity_threshold:
                    for k, v in related_labels.items():
                        if old_cls in v:
                            to_unfreeze.add(k)
                            print(f"⚠️ Unfreezing {k} due to low self-similarity of Class {old_cls}")

        # --- Default freeze all LoRA + fc2 ---
        for adapter in model.lora_adapters:
            for p in adapter.parameters():
                p.requires_grad = False
        for p in model.fc2.parameters():
            p.requires_grad = False

        # --- Unfreeze according to to_unfreeze ---
        for idx in to_unfreeze:
            if isinstance(idx, int):
                for p in model.lora_adapters[idx].parameters():
                    p.requires_grad = True
            elif idx == "fc2":
                for p in model.fc2.parameters():
                    p.requires_grad = True

        # --- Unfreeze new adapters (just added) ---
        for idx in new_lora_indices:
            for p in model.lora_adapters[idx].parameters():
                p.requires_grad = True

        for p in model.fc3.parameters():
            p.requires_grad = True

        print(f"\n📌 related_labels (after logic): {related_labels}")
        print(f"📌 to_unfreeze set: {to_unfreeze}")
        print(f"📌 new_lora_indices: {new_lora_indices}")

    # === Confirm trainable parameter status after freeze/unfreeze ===
    print("\n📐 Model Architecture:")
    print(model)

    print("\n🔧 Trainable Parameter Overview Before Training:")
    for name, param in model.named_parameters():
        status = "✅ trainable" if param.requires_grad else "❌ frozen"
        print(f"{name:<50} | {status:<12} | shape={list(param.shape)}")

    print("\n" + "=" * 80 + "\n")

    # 🧠 Optimizer setup
    optimizer = torch.optim.Adam(filter(lambda p: p.requires_grad, model.parameters()), lr=optimizer.param_groups[0]['lr'])

    # Full training loop continuation for train_with_dynex_clora
    for epoch in range(num_epochs):
        if stop_signal_file and os.path.exists(stop_signal_file):
            print("\n🛑 Stop signal detected. Exiting training loop.")
            break

        model.train()
        epoch_loss = 0.0
        class_correct, class_total = {}, {}

        for xb, yb in train_loader:
            optimizer.zero_grad()
            logits = model(xb).view(-1, output_size)
            yb_flat = yb.view(-1)
            ce_loss = criterion(logits, yb_flat)

            if teacher_model and stable_classes:
                with torch.no_grad():
                    teacher_logits = teacher_model(xb)
                student_stable = logits[:, stable_classes]
                teacher_stable = teacher_logits[:, stable_classes]
                distill_loss = F.mse_loss(student_stable, teacher_stable)
                total_loss = alpha * distill_loss + (1 - alpha) * ce_loss
            else:
                total_loss = ce_loss

            total_loss.backward()
            optimizer.step()
            epoch_loss += total_loss.item() * xb.size(0)
            compute_classwise_accuracy(logits, yb_flat, class_correct, class_total)

        train_loss = epoch_loss / len(train_loader.dataset)
        train_acc = {int(k): f"{(class_correct[k] / class_total[k]) * 100:.2f}%" if class_total[k] > 0 else "0.00%" for k in class_total}

        # === Validation ===
        model.eval()
        val_loss, val_correct, val_total = 0.0, 0, 0
        val_class_correct, val_class_total = {}, {}

        with torch.no_grad():
            for xb, yb in val_loader:
                outputs = model(xb).view(-1, output_size)
                yb_flat = yb.view(-1)
                val_loss += criterion(outputs, yb_flat).item() * xb.size(0)
                preds = torch.argmax(outputs, dim=1)
                val_correct += (preds == yb_flat).sum().item()
                val_total += yb_flat.size(0)
                compute_classwise_accuracy(outputs, yb_flat, val_class_correct, val_class_total)

        val_loss /= len(val_loader.dataset)
        val_acc = val_correct / val_total
        val_acc_cls = {int(k): f"{(val_class_correct[k]/val_class_total[k])*100:.2f}%" if val_class_total[k]>0 else "0.00%" for k in val_class_total}

        print(f"Epoch {epoch+1}/{num_epochs}, Train Loss: {train_loss:.6f}, Train-Class-Acc: {train_acc}")
        print(f"Val Loss: {val_loss:.6f}, Val Acc: {val_acc*100:.2f}%, Val-Class-Acc: {val_acc_cls}, LR: {optimizer.param_groups[0]['lr']:.6f}")

        # === Save Current Epoch ===
        model_path = os.path.join(model_saving_folder, f"{model_name}_epoch_{epoch+1}.pth")
        current = {
            'epoch': epoch + 1,
            'train_loss': train_loss,
            'val_loss': val_loss,
            'val_accuracy': val_acc,
            'train_classwise_accuracy': train_acc,
            'val_classwise_accuracy': val_acc_cls,
            'model_state_dict': model.state_dict(),
            'optimizer_state_dict': optimizer.state_dict(),
            'learning_rate': optimizer.param_groups[0]['lr'],
            'model_path': model_path,
            'num_lora_adapters': len(model.lora_adapters),
            'related_labels': related_labels
        }

        if len(best_results) < 5 or val_acc > best_results[-1]['val_accuracy']:
            if len(best_results) == 5:
                to_remove = best_results.pop()
                if os.path.exists(to_remove['model_path']):
                    os.remove(to_remove['model_path'])
                    print(f"🗑 Removed: {to_remove['model_path']}")
            best_results.append(current)
            best_results.sort(key=lambda x: (x['val_accuracy'], x['epoch']), reverse=True)
            torch.save(current, model_path)
            print(f"✅ Saved model: {model_path}")

        if scheduler: scheduler.step(val_loss)

    elapsed_time = time.time() - start_time
    print(f"\n⏳ Total training time: {elapsed_time:.2f} seconds")

    if best_results:
        best = best_results[0]
        best_model_path = os.path.join(model_saving_folder, f"{model_name}_best.pth")
        torch.save(best, best_model_path)
        print(f"\n🏆 Best model saved as: {best_model_path} (Val Accuracy: {best['val_accuracy'] * 100:.2f}%)")

    final_model_path = os.path.join(model_saving_folder, f"{model_name}_final.pth")
    torch.save(current, final_model_path)
    print(f"\n📌 Final model saved as: {final_model_path}")

    print("\n🎯 Top 5 Best Models:")
    for res in best_results:
        print(f"Epoch {res['epoch']}, Train Loss: {res['train_loss']:.6f}, Train-Acc: {res['train_classwise_accuracy']},\n"
              f"Val Loss: {res['val_loss']:.6f}, Val Acc: {res['val_accuracy']*100:.2f}%, Val-Acc: {res['val_classwise_accuracy']}, Model Path: {res['model_path']}")

    match = re.search(r'Period_(\d+)', model_saving_folder)
    period_label = match.group(1) if match else str(period)
    model_name_str = model.__class__.__name__
    best_model = max(best_results, key=lambda x: x['val_accuracy'])

    best_md_summary = f"""
    ---
### Period {period_label} (alpha = {alpha}, similarity_threshold = {similarity_threshold})
+ ##### Total training time: {elapsed_time:.2f} seconds
+ ##### Model: {model_name_str}
+ ##### Training and saving in *'{model_saving_folder}'*
+ ##### Best Epoch: {best_model['epoch']}
#### __Val Accuracy: {best_model['val_accuracy'] * 100:.2f}%__
#### __Val-Class-Acc: {best_model['val_classwise_accuracy']}__
    """
    print(best_md_summary.strip())

    if class_features_dict is None:
        class_features_dict = {}
    class_features_dict.update(new_class_features)
    with open(os.path.join(model_saving_folder, "class_features.pkl"), 'wb') as f:
        pickle.dump(class_features_dict, f)
    print(f"Saved class features to: {os.path.join(model_saving_folder, 'class_features.pkl')}")

    torch.cuda.empty_cache()
    gc.collect()



## __📋 Label Mapping (HAR Activities)__

| Label ID | Activity Name       |
|----------|---------------------|
|    0     | SITTING             |
|    1     | STANDING            |
|    2     | WALKING             |
|    3     | LAYING              |
|    4     | WALKING_UPSTAIRS    |
|    5     | WALKING_DOWNSTAIRS  |

## __Common Parameters__

In [15]:
batch_size = 32
stop_signal_file = os.path.normpath(os.path.join('Class_Incremental_CL', 'HAR_CIL/stop_training.txt'))

## __~~~ AVERAGE Test ~~~__

## __HAR_MLP_v2 Training (alpha = 0.1, similarity_threshold = 0.5)__

In [ ]:
similarity_threshold=0.5

---
### Period 1 (alpha = 0.1, similarity_threshold = 0.5)
+ ##### Total training time: 147.35 seconds
+ ##### Model: HAR_MLP_LoRA_v2
+ ##### Training and saving in *'Class_Incremental_CL/HAR_CIL/Trained_models/DynEx_CLoRA/alpha_0.1/sim_thd_0.5/Period_1'*
+ ##### Best Epoch: 955
#### __Val Accuracy: 94.62%__
#### __Val-Class-Acc: {0: '91.45%', 1: '97.56%'}__

In [39]:
# ================================
# 📌 Period 1 Configuration - HAR_MLP_LoRA_v2
# ================================
period = 1

# Load dataset for this period
X_train, y_train = period_datasets[period]["train"]
X_val, y_val     = period_datasets[period]["test"]

# Auto-select CUDA device
device = auto_select_cuda_device()

# Model and training hyperparameters
input_size    = X_train.shape[1]
hidden_size   = 128
output_size   = len(set(y_train))
dropout       = 0.2
learning_rate = 0.0001
weight_decay  = 1e-5
num_epochs    = 1000
alpha         = 0.1  # Not used in Period 1 but passed for compatibility
teacher_model = None
stable_classes = None

# Model saving path
model_name = "HAR_MLP_LoRA_v2"
model_saving_folder = os.path.join(
    "Class_Incremental_CL", "HAR_CIL", "Trained_models", 
    "DynEx_CLoRA", f"alpha_{alpha}", f"sim_thd_{similarity_threshold}", f"Period_{period}"
)
os.makedirs(model_saving_folder, exist_ok=True)

# Initialize model, criterion, optimizer
student_model = HAR_MLP_LoRA_v2(
    input_size=input_size,
    hidden_size=hidden_size,
    output_size=output_size,
    dropout=dropout,
    lora_rank=4  # or whatever value you want
).to(device)

criterion = nn.CrossEntropyLoss()
optimizer = torch.optim.Adam(student_model.parameters(), lr=learning_rate, weight_decay=weight_decay)
scheduler = None

# Train the model
train_with_dynex_clora(
    model=student_model,
    teacher_model=teacher_model,
    output_size=output_size,
    criterion=criterion,
    optimizer=optimizer,
    X_train=X_train,
    y_train=y_train,
    X_val=X_val,
    y_val=y_val,
    num_epochs=num_epochs,
    batch_size=batch_size,
    alpha=alpha,
    model_saving_folder=model_saving_folder,
    model_name=model_name,
    stop_signal_file=stop_signal_file,
    scheduler=scheduler,
    period=period,
    stable_classes=stable_classes,
    class_features_dict=None,
    related_labels={"fc2": [0, 1]},  # Period 1 的初始化
    similarity_threshold=similarity_threshold
)

# ================================
# ✅ Summary & Resource Cleanup
# ================================
unique_classes = np.unique(y_train)
num_classes = len(unique_classes)

print(f"\n✅ Period {period} Training Complete. Final model architecture:")
print(student_model)
print(f"📊 Class Summary → unique_classes = {unique_classes}, num_classes = {num_classes}")

del X_train, y_train, X_val, y_val, teacher_model, student_model
gc.collect()
torch.cuda.empty_cache()


🎯 Automatically selected GPU:
    - CUDA Device ID : 1
    - Memory Used    : 1124 MiB
    - Device Name    : NVIDIA RTX A6000

🚀 'train_with_dynex_clora' started for Period 1

✅ Removed existing folder: Class_Incremental_CL/HAR_CIL/Trained_models/DynEx_CLoRA/alpha_0.1/sim_thd_0.5/Period_1
🎯 Automatically selected GPU:
    - CUDA Device ID : 1
    - Memory Used    : 1124 MiB
    - Device Name    : NVIDIA RTX A6000

✅ Data Overview:
X_train: torch.Size([2660, 561]), y_train: torch.Size([2660])
X_val: torch.Size([1023, 561]), y_val: torch.Size([1023])

📐 Model Architecture:
HAR_MLP_LoRA_v2(
  (fc1): Linear(in_features=561, out_features=128, bias=True)
  (bn1): BatchNorm1d(128, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  (relu1): ReLU()
  (dropout1): Dropout(p=0.2, inplace=False)
  (fc2): Linear(in_features=128, out_features=128, bias=True)
  (lora_adapters): ModuleList()
  (bn2): BatchNorm1d(128, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  (rel

---
### Period 2 (alpha = 0.1, similarity_threshold = 0.5)
+ ##### Total training time: 416.32 seconds
+ ##### Model: HAR_MLP_LoRA_v2
+ ##### Training and saving in *'Class_Incremental_CL/HAR_CIL/Trained_models/DynEx_CLoRA/alpha_0.1/sim_thd_0.5/Period_2'*
+ ##### Best Epoch: 600
#### __Val Accuracy: 97.72%__
#### __Val-Class-Acc: {0: '93.48%', 1: '95.68%', 2: '100.00%'}__

In [42]:
# ================================
# 📌 Period 2 Configuration - HAR_MLP_LoRA_v2
# ================================
period = 2

X_train, y_train = period_datasets[period]["train"]
X_val, y_val     = period_datasets[period]["test"]

device = auto_select_cuda_device()

input_size    = X_train.shape[1]
hidden_size   = 128
output_size   = len(set(y_train))
dropout       = 0.2
learning_rate = 0.0001
weight_decay  = 1e-5
num_epochs    = 1000
alpha         = 0.1
stable_classes = [0, 1]  # 根據 Period 1 類別定義

model_name = "HAR_MLP_LoRA_v2"
model_saving_folder = os.path.join(
    "Class_Incremental_CL", "HAR_CIL", "Trained_models", 
    "DynEx_CLoRA", f"alpha_{alpha}", f"sim_thd_{similarity_threshold}", f"Period_{period}"
)
os.makedirs(model_saving_folder, exist_ok=True)

# Load previous class features
prev_folder = os.path.join(
    "Class_Incremental_CL", "HAR_CIL", "Trained_models", 
    "DynEx_CLoRA", f"alpha_{alpha}", f"sim_thd_{similarity_threshold}", f"Period_{period - 1}"
)
class_features_path = os.path.join(prev_folder, "class_features.pkl")
if os.path.exists(class_features_path):
    with open(class_features_path, 'rb') as f:
        class_features_dict = pickle.load(f)
    print(f"✅ Loaded class features from: {class_features_path}")
else:
    class_features_dict = {}
    print("⚠️ No previous class features found.")

# Load previous model as teacher
teacher_checkpoint_path = os.path.join(prev_folder, f"{model_name}_best.pth")
teacher_model = HAR_MLP_LoRA_v2(
    input_size=input_size,
    hidden_size=hidden_size,
    output_size=output_size - 1,  # Exclude new class
    dropout=dropout,
    lora_rank=4
).to(device)

checkpoint = torch.load(teacher_checkpoint_path, map_location=device)
num_lora_adapters = checkpoint.get("num_lora_adapters", 0)
print(f"Teacher model num_lora_adapters: {num_lora_adapters}")
related_labels = checkpoint.get("related_labels", {"fc2": [0, 1]})
print(f"Teacher checkpoint has {num_lora_adapters} LoRA adapters.")

for _ in range(num_lora_adapters):
    teacher_model.add_lora_adapter()
teacher_model.load_state_dict(checkpoint["model_state_dict"])
del checkpoint

# Instantiate student and initialize from teacher (except fc3)
student_model = HAR_MLP_LoRA_v2(
    input_size=input_size,
    hidden_size=hidden_size,
    output_size=output_size,
    dropout=dropout,
    lora_rank=4
).to(device)

for _ in range(num_lora_adapters):
    student_model.add_lora_adapter()

# Copy shared weights
teacher_dict = teacher_model.state_dict()
student_dict = student_model.state_dict()
for name, param in teacher_dict.items():
    if not name.startswith("fc3"):
        student_dict[name].copy_(param)
student_model.load_state_dict(student_dict)

# Train setup
criterion = nn.CrossEntropyLoss()
optimizer = torch.optim.Adam(student_model.parameters(), lr=learning_rate, weight_decay=weight_decay)
scheduler = None

# Train
train_with_dynex_clora(
    model=student_model,
    teacher_model=teacher_model,
    output_size=output_size,
    criterion=criterion,
    optimizer=optimizer,
    X_train=X_train,
    y_train=y_train,
    X_val=X_val,
    y_val=y_val,
    num_epochs=num_epochs,
    batch_size=batch_size,
    alpha=alpha,
    model_saving_folder=model_saving_folder,
    model_name=model_name,
    stop_signal_file=stop_signal_file,
    scheduler=scheduler,
    period=period,
    stable_classes=stable_classes,
    class_features_dict=class_features_dict,
    related_labels=related_labels,
    logic_version="average",  # or "all"
    similarity_threshold=similarity_threshold
)

# Cleanup
unique_classes = np.unique(y_train)
print(f"\nstudent_model summary:\n{student_model}")
print(f"unique_classes = {unique_classes}, num_classes = {len(unique_classes)}")

del X_train, y_train, X_val, y_val, teacher_model, student_model, teacher_dict, student_dict, teacher_checkpoint_path
gc.collect()
torch.cuda.empty_cache()


🎯 Automatically selected GPU:
    - CUDA Device ID : 1
    - Memory Used    : 1124 MiB
    - Device Name    : NVIDIA RTX A6000
✅ Loaded class features from: Class_Incremental_CL/HAR_CIL/Trained_models/DynEx_CLoRA/alpha_0.1/sim_thd_0.5/Period_1/class_features.pkl
Teacher model num_lora_adapters: 0
Teacher checkpoint has 0 LoRA adapters.

🚀 'train_with_dynex_clora' started for Period 2

✅ Removed existing folder: Class_Incremental_CL/HAR_CIL/Trained_models/DynEx_CLoRA/alpha_0.1/sim_thd_0.5/Period_2
🎯 Automatically selected GPU:
    - CUDA Device ID : 1
    - Memory Used    : 1124 MiB
    - Device Name    : NVIDIA RTX A6000

✅ Data Overview:
X_train: torch.Size([5945, 561]), y_train: torch.Size([5945])
X_val: torch.Size([2410, 561]), y_val: torch.Size([2410])


/tmp/ipykernel_680917/2766794092.py:52: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  checkpoint = torch.load(teacher_checkpoint_path, map_location=device)



🔎 Similarity Scores:
New Class 0:
  - Existing Class 0: 0.5146
  - Existing Class 1: 0.5001
New Class 1:
  - Existing Class 0: 0.4351
  - Existing Class 1: 0.4526
New Class 2:
  - Existing Class 0: 0.3400
  - Existing Class 1: 0.3387
📊 Average similarity: 0.4302, Std: 0.0696
🧩 Similarity threshold: 0.5
👥 Existing classes: [0, 1]
🆕 New classes: [0, 1, 2]
🧩 New classes detected (for LoRA decision): [2]
[Similarity] Class 2 - Avg Sim = 0.3394
✅ Added LoRA adapter to HAR_MLP_LoRA_v2 (fc2), total adapters: 1
[Stability Check] Class 0 similarity with itself: 0.5146
[Stability Check] Class 1 similarity with itself: 0.4526
⚠️ Unfreezing fc2 due to low self-similarity of Class 1

📌 related_labels (after logic): {'fc2': [0, 1], 0: [2]}
📌 to_unfreeze set: {'fc2'}
📌 new_lora_indices: [0]

📐 Model Architecture:
HAR_MLP_LoRA_v2(
  (fc1): Linear(in_features=561, out_features=128, bias=True)
  (bn1): BatchNorm1d(128, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  (relu1): ReLU()
  

---
### Period 3 (alpha = 0.1, similarity_threshold = 0.5)
+ ##### Total training time: 567.35 seconds
+ ##### Model: HAR_MLP_LoRA_v2
+ ##### Training and saving in *'Class_Incremental_CL/HAR_CIL/Trained_models/DynEx_CLoRA/alpha_0.1/sim_thd_0.5/Period_3'*
+ ##### Best Epoch: 724
#### __Val Accuracy: 98.30%__
#### __Val-Class-Acc: {0: '94.30%', 1: '95.86%', 3: '100.00%', 2: '100.00%'}__

In [45]:
# ================================
# 📌 Period 3 Configuration - HAR_MLP_LoRA_v2
# ================================
period = 3

X_train, y_train = period_datasets[period]["train"]
X_val, y_val     = period_datasets[period]["test"]

input_size    = X_train.shape[1]
hidden_size   = 128
output_size   = len(set(y_train))
dropout       = 0.2
learning_rate = 0.0001
weight_decay  = 1e-5
num_epochs    = 1000
alpha         = 0.1
stable_classes = [0, 1, 2]

model_name = "HAR_MLP_LoRA_v2"
model_saving_folder = os.path.join(
    "Class_Incremental_CL", "HAR_CIL", "Trained_models", 
    "DynEx_CLoRA", f"alpha_{alpha}", f"sim_thd_{similarity_threshold}", f"Period_{period}"
)
os.makedirs(model_saving_folder, exist_ok=True)

prev_folder = os.path.join(
    "Class_Incremental_CL", "HAR_CIL", "Trained_models", 
    "DynEx_CLoRA", f"alpha_{alpha}", f"sim_thd_{similarity_threshold}", f"Period_{period - 1}"
)
class_features_path = os.path.join(prev_folder, "class_features.pkl")
if os.path.exists(class_features_path):
    with open(class_features_path, 'rb') as f:
        class_features_dict = pickle.load(f)
    print(f"✅ Loaded class features from: {class_features_path}")
else:
    class_features_dict = {}
    print("⚠️ No previous class features found.")

teacher_checkpoint_path = os.path.join(prev_folder, f"{model_name}_best.pth")
teacher_model = HAR_MLP_LoRA_v2(
    input_size=input_size,
    hidden_size=hidden_size,
    output_size=output_size - 1,
    dropout=dropout,
    lora_rank=4
).to(device)

checkpoint = torch.load(teacher_checkpoint_path, map_location=device)
num_lora_adapters = checkpoint.get("num_lora_adapters", 0)
related_labels = checkpoint.get("related_labels", {"fc2": [0, 1]})
for _ in range(num_lora_adapters):
    teacher_model.add_lora_adapter()
teacher_model.load_state_dict(checkpoint["model_state_dict"])
del checkpoint

student_model = HAR_MLP_LoRA_v2(
    input_size=input_size,
    hidden_size=hidden_size,
    output_size=output_size,
    dropout=dropout,
    lora_rank=4
).to(device)
for _ in range(num_lora_adapters):
    student_model.add_lora_adapter()

teacher_dict = teacher_model.state_dict()
student_dict = student_model.state_dict()
for name, param in teacher_dict.items():
    if not name.startswith("fc3"):
        student_dict[name].copy_(param)
student_model.load_state_dict(student_dict)

criterion = nn.CrossEntropyLoss()
optimizer = torch.optim.Adam(student_model.parameters(), lr=learning_rate, weight_decay=weight_decay)
scheduler = None

train_with_dynex_clora(
    model=student_model,
    teacher_model=teacher_model,
    output_size=output_size,
    criterion=criterion,
    optimizer=optimizer,
    X_train=X_train,
    y_train=y_train,
    X_val=X_val,
    y_val=y_val,
    num_epochs=num_epochs,
    batch_size=batch_size,
    alpha=alpha,
    model_saving_folder=model_saving_folder,
    model_name=model_name,
    stop_signal_file=stop_signal_file,
    scheduler=scheduler,
    period=period,
    stable_classes=stable_classes,
    class_features_dict=class_features_dict,
    related_labels=related_labels,
    logic_version="average",
    similarity_threshold=similarity_threshold
)

unique_classes = np.unique(y_train)
print(f"\nstudent_model summary:\n{student_model}")
print(f"unique_classes = {unique_classes}, num_classes = {len(unique_classes)}")

del X_train, y_train, X_val, y_val, teacher_model, student_model, teacher_dict, student_dict, teacher_checkpoint_path
gc.collect()
torch.cuda.empty_cache()


✅ Loaded class features from: Class_Incremental_CL/HAR_CIL/Trained_models/DynEx_CLoRA/alpha_0.1/sim_thd_0.5/Period_2/class_features.pkl
✅ Added LoRA adapter to HAR_MLP_LoRA_v2 (fc2), total adapters: 1
✅ Added LoRA adapter to HAR_MLP_LoRA_v2 (fc2), total adapters: 1

🚀 'train_with_dynex_clora' started for Period 3

✅ Removed existing folder: Class_Incremental_CL/HAR_CIL/Trained_models/DynEx_CLoRA/alpha_0.1/sim_thd_0.5/Period_3


/tmp/ipykernel_680917/4255337735.py:48: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  checkpoint = torch.load(teacher_checkpoint_path, map_location=device)


🎯 Automatically selected GPU:
    - CUDA Device ID : 1
    - Memory Used    : 36599 MiB
    - Device Name    : NVIDIA RTX A6000

✅ Data Overview:
X_train: torch.Size([7352, 561]), y_train: torch.Size([7352])
X_val: torch.Size([2947, 561]), y_val: torch.Size([2947])

🔎 Similarity Scores:
New Class 0:
  - Existing Class 0: 0.8222
  - Existing Class 1: 0.3811
  - Existing Class 2: 0.4034
New Class 1:
  - Existing Class 0: 0.4728
  - Existing Class 1: 0.7081
  - Existing Class 2: 0.2853
New Class 2:
  - Existing Class 0: 0.7242
  - Existing Class 1: 0.7719
  - Existing Class 2: 0.6622
New Class 3:
  - Existing Class 0: 0.5362
  - Existing Class 1: 0.4260
  - Existing Class 2: 0.3887
📊 Average similarity: 0.5485, Std: 0.1729
🧩 Similarity threshold: 0.5
👥 Existing classes: [0, 1, 2]
🆕 New classes: [0, 1, 2, 3]
🧩 New classes detected (for LoRA decision): [3]
[Similarity] Class 3 - Avg Sim = 0.4503
✅ Added LoRA adapter to HAR_MLP_LoRA_v2 (fc2), total adapters: 2
🔄 New Class 3 is similar to Old

---
### Period 4 (alpha = 0.1, similarity_threshold = 0.5)
+ ##### Total training time: 582.08 seconds
+ ##### Model: HAR_MLP_LoRA_v2
+ ##### Training and saving in *'Class_Incremental_CL/HAR_CIL/Trained_models/DynEx_CLoRA/alpha_0.1/sim_thd_0.5/Period_4'*
+ ##### Best Epoch: 695
#### __Val Accuracy: 97.15%__
#### __Val-Class-Acc: {0: '91.24%', 1: '97.18%', 3: '100.00%', 2: '99.60%', 5: '98.10%', 4: '96.60%'}__

In [47]:
# ================================
# 📌 Period 4 Configuration - HAR_MLP_LoRA_v2
# ================================
period = 4

X_train, y_train = period_datasets[period]["train"]
X_val, y_val     = period_datasets[period]["test"]

input_size    = X_train.shape[1]
hidden_size   = 128
output_size   = len(set(y_train))
dropout       = 0.2
learning_rate = 0.0001
weight_decay  = 1e-5
num_epochs    = 1000
alpha         = 0.1
stable_classes = [0, 1, 3]

model_name = "HAR_MLP_LoRA_v2"
model_saving_folder = os.path.join(
    "Class_Incremental_CL", "HAR_CIL", "Trained_models", 
    "DynEx_CLoRA", f"alpha_{alpha}", f"sim_thd_{similarity_threshold}", f"Period_{period}"
)
os.makedirs(model_saving_folder, exist_ok=True)

prev_folder = os.path.join(
    "Class_Incremental_CL", "HAR_CIL", "Trained_models", 
    "DynEx_CLoRA", f"alpha_{alpha}", f"sim_thd_{similarity_threshold}", f"Period_{period - 1}"
)
class_features_path = os.path.join(prev_folder, "class_features.pkl")
if os.path.exists(class_features_path):
    with open(class_features_path, 'rb') as f:
        class_features_dict = pickle.load(f)
    print(f"✅ Loaded class features from: {class_features_path}")
else:
    class_features_dict = {}
    print("⚠️ No previous class features found.")

teacher_checkpoint_path = os.path.join(prev_folder, f"{model_name}_best.pth")
teacher_model = HAR_MLP_LoRA_v2(
    input_size=input_size,
    hidden_size=hidden_size,
    output_size=output_size - 2,
    dropout=dropout,
    lora_rank=4
).to(device)

checkpoint = torch.load(teacher_checkpoint_path, map_location=device)
num_lora_adapters = checkpoint.get("num_lora_adapters", 0)
related_labels = checkpoint.get("related_labels", {"fc2": [0, 1]})
for _ in range(num_lora_adapters):
    teacher_model.add_lora_adapter()
teacher_model.load_state_dict(checkpoint["model_state_dict"])
del checkpoint

student_model = HAR_MLP_LoRA_v2(
    input_size=input_size,
    hidden_size=hidden_size,
    output_size=output_size,
    dropout=dropout,
    lora_rank=4
).to(device)
for _ in range(num_lora_adapters):
    student_model.add_lora_adapter()

teacher_dict = teacher_model.state_dict()
student_dict = student_model.state_dict()
for name, param in teacher_dict.items():
    if not name.startswith("fc3"):
        student_dict[name].copy_(param)
student_model.load_state_dict(student_dict)

criterion = nn.CrossEntropyLoss()
optimizer = torch.optim.Adam(student_model.parameters(), lr=learning_rate, weight_decay=weight_decay)
scheduler = None

train_with_dynex_clora(
    model=student_model,
    teacher_model=teacher_model,
    output_size=output_size,
    criterion=criterion,
    optimizer=optimizer,
    X_train=X_train,
    y_train=y_train,
    X_val=X_val,
    y_val=y_val,
    num_epochs=num_epochs,
    batch_size=batch_size,
    alpha=alpha,
    model_saving_folder=model_saving_folder,
    model_name=model_name,
    stop_signal_file=stop_signal_file,
    scheduler=scheduler,
    period=period,
    stable_classes=stable_classes,
    class_features_dict=class_features_dict,
    related_labels=related_labels,
    logic_version="average",
    similarity_threshold=similarity_threshold
)

unique_classes = np.unique(y_train)
print(f"\nstudent_model summary:\n{student_model}")
print(f"unique_classes = {unique_classes}, num_classes = {len(unique_classes)}")

del X_train, y_train, X_val, y_val, teacher_model, student_model, teacher_dict, student_dict, teacher_checkpoint_path
gc.collect()
torch.cuda.empty_cache()


✅ Loaded class features from: Class_Incremental_CL/HAR_CIL/Trained_models/DynEx_CLoRA/alpha_0.1/sim_thd_0.5/Period_3/class_features.pkl
✅ Added LoRA adapter to HAR_MLP_LoRA_v2 (fc2), total adapters: 1
✅ Added LoRA adapter to HAR_MLP_LoRA_v2 (fc2), total adapters: 2
✅ Added LoRA adapter to HAR_MLP_LoRA_v2 (fc2), total adapters: 1
✅ Added LoRA adapter to HAR_MLP_LoRA_v2 (fc2), total adapters: 2

🚀 'train_with_dynex_clora' started for Period 4

✅ Removed existing folder: Class_Incremental_CL/HAR_CIL/Trained_models/DynEx_CLoRA/alpha_0.1/sim_thd_0.5/Period_4


/tmp/ipykernel_680917/1575189348.py:48: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  checkpoint = torch.load(teacher_checkpoint_path, map_location=device)


🎯 Automatically selected GPU:
    - CUDA Device ID : 1
    - Memory Used    : 1128 MiB
    - Device Name    : NVIDIA RTX A6000

✅ Data Overview:
X_train: torch.Size([7352, 561]), y_train: torch.Size([7352])
X_val: torch.Size([2947, 561]), y_val: torch.Size([2947])

🔎 Similarity Scores:
New Class 0:
  - Existing Class 0: 0.6813
  - Existing Class 1: 0.3302
  - Existing Class 2: 0.5897
  - Existing Class 3: 0.4143
New Class 1:
  - Existing Class 0: 0.3451
  - Existing Class 1: 0.6273
  - Existing Class 2: 0.5474
  - Existing Class 3: 0.2689
New Class 2:
  - Existing Class 0: 0.4721
  - Existing Class 1: 0.3222
  - Existing Class 2: 0.6499
  - Existing Class 3: 0.3400
New Class 3:
  - Existing Class 0: 0.4944
  - Existing Class 1: 0.4422
  - Existing Class 2: 0.6165
  - Existing Class 3: 0.6025
New Class 4:
  - Existing Class 0: 0.3068
  - Existing Class 1: 0.2891
  - Existing Class 2: 0.6128
  - Existing Class 3: 0.2398
New Class 5:
  - Existing Class 0: 0.4385
  - Existing Class 1: 0.30

## __HAR_MLP_v2 Training (alpha = 0.2, similarity_threshold = 0.5)__

In [50]:
similarity_threshold=0.5

---
### Period 1 (alpha = 0.2, similarity_threshold = 0.5)
+ ##### Total training time: 135.81 seconds
+ ##### Model: HAR_MLP_LoRA_v2
+ ##### Training and saving in *'Class_Incremental_CL/HAR_CIL/Trained_models/DynEx_CLoRA/alpha_0.2/sim_thd_0.5/Period_1'*
+ ##### Best Epoch: 157
#### __Val Accuracy: 95.31%__
#### __Val-Class-Acc: {0: '92.46%', 1: '97.93%'}__

In [51]:
# ================================
# 📌 Period 1 Configuration - HAR_MLP_LoRA_v2
# ================================
period = 1

# Load dataset for this period
X_train, y_train = period_datasets[period]["train"]
X_val, y_val     = period_datasets[period]["test"]

# Auto-select CUDA device
device = auto_select_cuda_device()

# Model and training hyperparameters
input_size    = X_train.shape[1]
hidden_size   = 128
output_size   = len(set(y_train))
dropout       = 0.2
learning_rate = 0.0001
weight_decay  = 1e-5
num_epochs    = 1000
alpha         = 0.2  # Not used in Period 1 but passed for compatibility
teacher_model = None
stable_classes = None

# Model saving path
model_name = "HAR_MLP_LoRA_v2"
model_saving_folder = os.path.join(
    "Class_Incremental_CL", "HAR_CIL", "Trained_models", 
    "DynEx_CLoRA", f"alpha_{alpha}", f"sim_thd_{similarity_threshold}", f"Period_{period}"
)
os.makedirs(model_saving_folder, exist_ok=True)

# Initialize model, criterion, optimizer
student_model = HAR_MLP_LoRA_v2(
    input_size=input_size,
    hidden_size=hidden_size,
    output_size=output_size,
    dropout=dropout,
    lora_rank=4  # or whatever value you want
).to(device)

criterion = nn.CrossEntropyLoss()
optimizer = torch.optim.Adam(student_model.parameters(), lr=learning_rate, weight_decay=weight_decay)
scheduler = None

# Train the model
train_with_dynex_clora(
    model=student_model,
    teacher_model=teacher_model,
    output_size=output_size,
    criterion=criterion,
    optimizer=optimizer,
    X_train=X_train,
    y_train=y_train,
    X_val=X_val,
    y_val=y_val,
    num_epochs=num_epochs,
    batch_size=batch_size,
    alpha=alpha,
    model_saving_folder=model_saving_folder,
    model_name=model_name,
    stop_signal_file=stop_signal_file,
    scheduler=scheduler,
    period=period,
    stable_classes=stable_classes,
    class_features_dict=None,
    related_labels={"fc2": [0, 1]},  # Period 1 的初始化
    similarity_threshold=similarity_threshold
)

# ================================
# ✅ Summary & Resource Cleanup
# ================================
unique_classes = np.unique(y_train)
num_classes = len(unique_classes)

print(f"\n✅ Period {period} Training Complete. Final model architecture:")
print(student_model)
print(f"📊 Class Summary → unique_classes = {unique_classes}, num_classes = {num_classes}")

del X_train, y_train, X_val, y_val, teacher_model, student_model
gc.collect()
torch.cuda.empty_cache()


🎯 Automatically selected GPU:
    - CUDA Device ID : 1
    - Memory Used    : 1110 MiB
    - Device Name    : NVIDIA RTX A6000

🚀 'train_with_dynex_clora' started for Period 1

✅ Removed existing folder: Class_Incremental_CL/HAR_CIL/Trained_models/DynEx_CLoRA/alpha_0.2/sim_thd_0.5/Period_1
🎯 Automatically selected GPU:
    - CUDA Device ID : 1
    - Memory Used    : 1110 MiB
    - Device Name    : NVIDIA RTX A6000

✅ Data Overview:
X_train: torch.Size([2660, 561]), y_train: torch.Size([2660])
X_val: torch.Size([1023, 561]), y_val: torch.Size([1023])

📐 Model Architecture:
HAR_MLP_LoRA_v2(
  (fc1): Linear(in_features=561, out_features=128, bias=True)
  (bn1): BatchNorm1d(128, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  (relu1): ReLU()
  (dropout1): Dropout(p=0.2, inplace=False)
  (fc2): Linear(in_features=128, out_features=128, bias=True)
  (lora_adapters): ModuleList()
  (bn2): BatchNorm1d(128, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  (rel

---
### Period 2 (alpha = 0.2, similarity_threshold = 0.5)
+ ##### Total training time: 420.31 seconds
+ ##### Model: HAR_MLP_LoRA_v2
+ ##### Training and saving in *'Class_Incremental_CL/HAR_CIL/Trained_models/DynEx_CLoRA/alpha_0.2/sim_thd_0.5/Period_2'*
+ ##### Best Epoch: 873
#### __Val Accuracy: 97.84%__
#### __Val-Class-Acc: {0: '93.08%', 1: '96.62%', 2: '100.00%'}__

In [52]:
# ================================
# 📌 Period 2 Configuration - HAR_MLP_LoRA_v2
# ================================
period = 2

X_train, y_train = period_datasets[period]["train"]
X_val, y_val     = period_datasets[period]["test"]

device = auto_select_cuda_device()

input_size    = X_train.shape[1]
hidden_size   = 128
output_size   = len(set(y_train))
dropout       = 0.2
learning_rate = 0.0001
weight_decay  = 1e-5
num_epochs    = 1000
alpha         = 0.2
stable_classes = [0, 1]  # 根據 Period 1 類別定義

model_name = "HAR_MLP_LoRA_v2"
model_saving_folder = os.path.join(
    "Class_Incremental_CL", "HAR_CIL", "Trained_models", 
    "DynEx_CLoRA", f"alpha_{alpha}", f"sim_thd_{similarity_threshold}", f"Period_{period}"
)
os.makedirs(model_saving_folder, exist_ok=True)

# Load previous class features
prev_folder = os.path.join(
    "Class_Incremental_CL", "HAR_CIL", "Trained_models", 
    "DynEx_CLoRA", f"alpha_{alpha}", f"sim_thd_{similarity_threshold}", f"Period_{period - 1}"
)
class_features_path = os.path.join(prev_folder, "class_features.pkl")
if os.path.exists(class_features_path):
    with open(class_features_path, 'rb') as f:
        class_features_dict = pickle.load(f)
    print(f"✅ Loaded class features from: {class_features_path}")
else:
    class_features_dict = {}
    print("⚠️ No previous class features found.")

# Load previous model as teacher
teacher_checkpoint_path = os.path.join(prev_folder, f"{model_name}_best.pth")
teacher_model = HAR_MLP_LoRA_v2(
    input_size=input_size,
    hidden_size=hidden_size,
    output_size=output_size - 1,  # Exclude new class
    dropout=dropout,
    lora_rank=4
).to(device)

checkpoint = torch.load(teacher_checkpoint_path, map_location=device)
num_lora_adapters = checkpoint.get("num_lora_adapters", 0)
print(f"Teacher model num_lora_adapters: {num_lora_adapters}")
related_labels = checkpoint.get("related_labels", {"fc2": [0, 1]})
print(f"Teacher checkpoint has {num_lora_adapters} LoRA adapters.")

for _ in range(num_lora_adapters):
    teacher_model.add_lora_adapter()
teacher_model.load_state_dict(checkpoint["model_state_dict"])
del checkpoint

# Instantiate student and initialize from teacher (except fc3)
student_model = HAR_MLP_LoRA_v2(
    input_size=input_size,
    hidden_size=hidden_size,
    output_size=output_size,
    dropout=dropout,
    lora_rank=4
).to(device)

for _ in range(num_lora_adapters):
    student_model.add_lora_adapter()

# Copy shared weights
teacher_dict = teacher_model.state_dict()
student_dict = student_model.state_dict()
for name, param in teacher_dict.items():
    if not name.startswith("fc3"):
        student_dict[name].copy_(param)
student_model.load_state_dict(student_dict)

# Train setup
criterion = nn.CrossEntropyLoss()
optimizer = torch.optim.Adam(student_model.parameters(), lr=learning_rate, weight_decay=weight_decay)
scheduler = None

# Train
train_with_dynex_clora(
    model=student_model,
    teacher_model=teacher_model,
    output_size=output_size,
    criterion=criterion,
    optimizer=optimizer,
    X_train=X_train,
    y_train=y_train,
    X_val=X_val,
    y_val=y_val,
    num_epochs=num_epochs,
    batch_size=batch_size,
    alpha=alpha,
    model_saving_folder=model_saving_folder,
    model_name=model_name,
    stop_signal_file=stop_signal_file,
    scheduler=scheduler,
    period=period,
    stable_classes=stable_classes,
    class_features_dict=class_features_dict,
    related_labels=related_labels,
    logic_version="average",  # or "all"
    similarity_threshold=similarity_threshold
)

# Cleanup
unique_classes = np.unique(y_train)
print(f"\nstudent_model summary:\n{student_model}")
print(f"unique_classes = {unique_classes}, num_classes = {len(unique_classes)}")

del X_train, y_train, X_val, y_val, teacher_model, student_model, teacher_dict, student_dict, teacher_checkpoint_path
gc.collect()
torch.cuda.empty_cache()


🎯 Automatically selected GPU:
    - CUDA Device ID : 1
    - Memory Used    : 1110 MiB
    - Device Name    : NVIDIA RTX A6000
✅ Loaded class features from: Class_Incremental_CL/HAR_CIL/Trained_models/DynEx_CLoRA/alpha_0.2/sim_thd_0.5/Period_1/class_features.pkl
Teacher model num_lora_adapters: 0
Teacher checkpoint has 0 LoRA adapters.

🚀 'train_with_dynex_clora' started for Period 2

✅ Removed existing folder: Class_Incremental_CL/HAR_CIL/Trained_models/DynEx_CLoRA/alpha_0.2/sim_thd_0.5/Period_2


/tmp/ipykernel_680917/1076905216.py:52: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  checkpoint = torch.load(teacher_checkpoint_path, map_location=device)


🎯 Automatically selected GPU:
    - CUDA Device ID : 1
    - Memory Used    : 1110 MiB
    - Device Name    : NVIDIA RTX A6000

✅ Data Overview:
X_train: torch.Size([5945, 561]), y_train: torch.Size([5945])
X_val: torch.Size([2410, 561]), y_val: torch.Size([2410])

🔎 Similarity Scores:
New Class 0:
  - Existing Class 0: 0.5133
  - Existing Class 1: 0.5007
New Class 1:
  - Existing Class 0: 0.4748
  - Existing Class 1: 0.4891
New Class 2:
  - Existing Class 0: 0.2908
  - Existing Class 1: 0.2894
📊 Average similarity: 0.4263, Std: 0.0970
🧩 Similarity threshold: 0.5
👥 Existing classes: [0, 1]
🆕 New classes: [0, 1, 2]
🧩 New classes detected (for LoRA decision): [2]
[Similarity] Class 2 - Avg Sim = 0.2901
✅ Added LoRA adapter to HAR_MLP_LoRA_v2 (fc2), total adapters: 1
[Stability Check] Class 0 similarity with itself: 0.5133
[Stability Check] Class 1 similarity with itself: 0.4891
⚠️ Unfreezing fc2 due to low self-similarity of Class 1

📌 related_labels (after logic): {'fc2': [0, 1], 0: [2]

---
### Period 3 (alpha = 0.2, similarity_threshold = 0.5)
+ ##### Total training time: 524.70 seconds
+ ##### Model: HAR_MLP_LoRA_v2
+ ##### Training and saving in *'Class_Incremental_CL/HAR_CIL/Trained_models/DynEx_CLoRA/alpha_0.2/sim_thd_0.5/Period_3'*
+ ##### Best Epoch: 123
#### __Val Accuracy: 98.20%__
#### __Val-Class-Acc: {0: '91.04%', 1: '98.31%', 3: '100.00%', 2: '100.00%'}__

In [53]:
# ================================
# 📌 Period 3 Configuration - HAR_MLP_LoRA_v2
# ================================
period = 3

X_train, y_train = period_datasets[period]["train"]
X_val, y_val     = period_datasets[period]["test"]

input_size    = X_train.shape[1]
hidden_size   = 128
output_size   = len(set(y_train))
dropout       = 0.2
learning_rate = 0.0001
weight_decay  = 1e-5
num_epochs    = 1000
alpha         = 0.2
stable_classes = [0, 1, 2]

model_name = "HAR_MLP_LoRA_v2"
model_saving_folder = os.path.join(
    "Class_Incremental_CL", "HAR_CIL", "Trained_models", 
    "DynEx_CLoRA", f"alpha_{alpha}", f"sim_thd_{similarity_threshold}", f"Period_{period}"
)
os.makedirs(model_saving_folder, exist_ok=True)

prev_folder = os.path.join(
    "Class_Incremental_CL", "HAR_CIL", "Trained_models", 
    "DynEx_CLoRA", f"alpha_{alpha}", f"sim_thd_{similarity_threshold}", f"Period_{period - 1}"
)
class_features_path = os.path.join(prev_folder, "class_features.pkl")
if os.path.exists(class_features_path):
    with open(class_features_path, 'rb') as f:
        class_features_dict = pickle.load(f)
    print(f"✅ Loaded class features from: {class_features_path}")
else:
    class_features_dict = {}
    print("⚠️ No previous class features found.")

teacher_checkpoint_path = os.path.join(prev_folder, f"{model_name}_best.pth")
teacher_model = HAR_MLP_LoRA_v2(
    input_size=input_size,
    hidden_size=hidden_size,
    output_size=output_size - 1,
    dropout=dropout,
    lora_rank=4
).to(device)

checkpoint = torch.load(teacher_checkpoint_path, map_location=device)
num_lora_adapters = checkpoint.get("num_lora_adapters", 0)
related_labels = checkpoint.get("related_labels", {"fc2": [0, 1]})
for _ in range(num_lora_adapters):
    teacher_model.add_lora_adapter()
teacher_model.load_state_dict(checkpoint["model_state_dict"])
del checkpoint

student_model = HAR_MLP_LoRA_v2(
    input_size=input_size,
    hidden_size=hidden_size,
    output_size=output_size,
    dropout=dropout,
    lora_rank=4
).to(device)
for _ in range(num_lora_adapters):
    student_model.add_lora_adapter()

teacher_dict = teacher_model.state_dict()
student_dict = student_model.state_dict()
for name, param in teacher_dict.items():
    if not name.startswith("fc3"):
        student_dict[name].copy_(param)
student_model.load_state_dict(student_dict)

criterion = nn.CrossEntropyLoss()
optimizer = torch.optim.Adam(student_model.parameters(), lr=learning_rate, weight_decay=weight_decay)
scheduler = None

train_with_dynex_clora(
    model=student_model,
    teacher_model=teacher_model,
    output_size=output_size,
    criterion=criterion,
    optimizer=optimizer,
    X_train=X_train,
    y_train=y_train,
    X_val=X_val,
    y_val=y_val,
    num_epochs=num_epochs,
    batch_size=batch_size,
    alpha=alpha,
    model_saving_folder=model_saving_folder,
    model_name=model_name,
    stop_signal_file=stop_signal_file,
    scheduler=scheduler,
    period=period,
    stable_classes=stable_classes,
    class_features_dict=class_features_dict,
    related_labels=related_labels,
    logic_version="average",
    similarity_threshold=similarity_threshold
)

unique_classes = np.unique(y_train)
print(f"\nstudent_model summary:\n{student_model}")
print(f"unique_classes = {unique_classes}, num_classes = {len(unique_classes)}")

del X_train, y_train, X_val, y_val, teacher_model, student_model, teacher_dict, student_dict, teacher_checkpoint_path
gc.collect()
torch.cuda.empty_cache()


✅ Loaded class features from: Class_Incremental_CL/HAR_CIL/Trained_models/DynEx_CLoRA/alpha_0.2/sim_thd_0.5/Period_2/class_features.pkl
✅ Added LoRA adapter to HAR_MLP_LoRA_v2 (fc2), total adapters: 1
✅ Added LoRA adapter to HAR_MLP_LoRA_v2 (fc2), total adapters: 1

🚀 'train_with_dynex_clora' started for Period 3

✅ Removed existing folder: Class_Incremental_CL/HAR_CIL/Trained_models/DynEx_CLoRA/alpha_0.2/sim_thd_0.5/Period_3
🎯 Automatically selected GPU:
    - CUDA Device ID : 1
    - Memory Used    : 25429 MiB
    - Device Name    : NVIDIA RTX A6000

✅ Data Overview:
X_train: torch.Size([7352, 561]), y_train: torch.Size([7352])
X_val: torch.Size([2947, 561]), y_val: torch.Size([2947])


/tmp/ipykernel_680917/3051095830.py:48: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  checkpoint = torch.load(teacher_checkpoint_path, map_location=device)



🔎 Similarity Scores:
New Class 0:
  - Existing Class 0: 0.7681
  - Existing Class 1: 0.4121
  - Existing Class 2: 0.3643
New Class 1:
  - Existing Class 0: 0.4636
  - Existing Class 1: 0.7410
  - Existing Class 2: 0.2272
New Class 2:
  - Existing Class 0: 0.7129
  - Existing Class 1: 0.8532
  - Existing Class 2: 0.6454
New Class 3:
  - Existing Class 0: 0.4877
  - Existing Class 1: 0.4466
  - Existing Class 2: 0.2104
📊 Average similarity: 0.5277, Std: 0.2043
🧩 Similarity threshold: 0.5
👥 Existing classes: [0, 1, 2]
🆕 New classes: [0, 1, 2, 3]
🧩 New classes detected (for LoRA decision): [3]
[Similarity] Class 3 - Avg Sim = 0.3816
✅ Added LoRA adapter to HAR_MLP_LoRA_v2 (fc2), total adapters: 2
[Stability Check] Class 0 similarity with itself: 0.7681
[Stability Check] Class 1 similarity with itself: 0.7410
[Stability Check] Class 2 similarity with itself: 0.6454

📌 related_labels (after logic): {'fc2': [0, 1], 0: [2], 1: [3]}
📌 to_unfreeze set: set()
📌 new_lora_indices: [1]

📐 Model Arc

---
### Period 4 (alpha = 0.2, similarity_threshold = 0.5)
+ ##### Total training time: 661.33 seconds
+ ##### Model: HAR_MLP_LoRA_v2
+ ##### Training and saving in *'Class_Incremental_CL/HAR_CIL/Trained_models/DynEx_CLoRA/alpha_0.2/sim_thd_0.5/Period_4'*
+ ##### Best Epoch: 914
#### __Val Accuracy: 96.91%__
#### __Val-Class-Acc: {0: '88.59%', 1: '98.68%', 3: '100.00%', 2: '99.60%', 5: '97.86%', 4: '96.39%'}__

In [54]:
# ================================
# 📌 Period 4 Configuration - HAR_MLP_LoRA_v2
# ================================
period = 4

X_train, y_train = period_datasets[period]["train"]
X_val, y_val     = period_datasets[period]["test"]

input_size    = X_train.shape[1]
hidden_size   = 128
output_size   = len(set(y_train))
dropout       = 0.2
learning_rate = 0.0001
weight_decay  = 1e-5
num_epochs    = 1000
alpha         = 0.2
stable_classes = [0, 1, 3]

model_name = "HAR_MLP_LoRA_v2"
model_saving_folder = os.path.join(
    "Class_Incremental_CL", "HAR_CIL", "Trained_models", 
    "DynEx_CLoRA", f"alpha_{alpha}", f"sim_thd_{similarity_threshold}", f"Period_{period}"
)
os.makedirs(model_saving_folder, exist_ok=True)

prev_folder = os.path.join(
    "Class_Incremental_CL", "HAR_CIL", "Trained_models", 
    "DynEx_CLoRA", f"alpha_{alpha}", f"sim_thd_{similarity_threshold}", f"Period_{period - 1}"
)
class_features_path = os.path.join(prev_folder, "class_features.pkl")
if os.path.exists(class_features_path):
    with open(class_features_path, 'rb') as f:
        class_features_dict = pickle.load(f)
    print(f"✅ Loaded class features from: {class_features_path}")
else:
    class_features_dict = {}
    print("⚠️ No previous class features found.")

teacher_checkpoint_path = os.path.join(prev_folder, f"{model_name}_best.pth")
teacher_model = HAR_MLP_LoRA_v2(
    input_size=input_size,
    hidden_size=hidden_size,
    output_size=output_size - 2,
    dropout=dropout,
    lora_rank=4
).to(device)

checkpoint = torch.load(teacher_checkpoint_path, map_location=device)
num_lora_adapters = checkpoint.get("num_lora_adapters", 0)
related_labels = checkpoint.get("related_labels", {"fc2": [0, 1]})
for _ in range(num_lora_adapters):
    teacher_model.add_lora_adapter()
teacher_model.load_state_dict(checkpoint["model_state_dict"])
del checkpoint

student_model = HAR_MLP_LoRA_v2(
    input_size=input_size,
    hidden_size=hidden_size,
    output_size=output_size,
    dropout=dropout,
    lora_rank=4
).to(device)
for _ in range(num_lora_adapters):
    student_model.add_lora_adapter()

teacher_dict = teacher_model.state_dict()
student_dict = student_model.state_dict()
for name, param in teacher_dict.items():
    if not name.startswith("fc3"):
        student_dict[name].copy_(param)
student_model.load_state_dict(student_dict)

criterion = nn.CrossEntropyLoss()
optimizer = torch.optim.Adam(student_model.parameters(), lr=learning_rate, weight_decay=weight_decay)
scheduler = None

train_with_dynex_clora(
    model=student_model,
    teacher_model=teacher_model,
    output_size=output_size,
    criterion=criterion,
    optimizer=optimizer,
    X_train=X_train,
    y_train=y_train,
    X_val=X_val,
    y_val=y_val,
    num_epochs=num_epochs,
    batch_size=batch_size,
    alpha=alpha,
    model_saving_folder=model_saving_folder,
    model_name=model_name,
    stop_signal_file=stop_signal_file,
    scheduler=scheduler,
    period=period,
    stable_classes=stable_classes,
    class_features_dict=class_features_dict,
    related_labels=related_labels,
    logic_version="average",
    similarity_threshold=similarity_threshold
)

unique_classes = np.unique(y_train)
print(f"\nstudent_model summary:\n{student_model}")
print(f"unique_classes = {unique_classes}, num_classes = {len(unique_classes)}")

del X_train, y_train, X_val, y_val, teacher_model, student_model, teacher_dict, student_dict, teacher_checkpoint_path
gc.collect()
torch.cuda.empty_cache()


✅ Loaded class features from: Class_Incremental_CL/HAR_CIL/Trained_models/DynEx_CLoRA/alpha_0.2/sim_thd_0.5/Period_3/class_features.pkl
✅ Added LoRA adapter to HAR_MLP_LoRA_v2 (fc2), total adapters: 1
✅ Added LoRA adapter to HAR_MLP_LoRA_v2 (fc2), total adapters: 2
✅ Added LoRA adapter to HAR_MLP_LoRA_v2 (fc2), total adapters: 1
✅ Added LoRA adapter to HAR_MLP_LoRA_v2 (fc2), total adapters: 2

🚀 'train_with_dynex_clora' started for Period 4

✅ Removed existing folder: Class_Incremental_CL/HAR_CIL/Trained_models/DynEx_CLoRA/alpha_0.2/sim_thd_0.5/Period_4
🎯 Automatically selected GPU:
    - CUDA Device ID : 1
    - Memory Used    : 1110 MiB
    - Device Name    : NVIDIA RTX A6000

✅ Data Overview:
X_train: torch.Size([7352, 561]), y_train: torch.Size([7352])
X_val: torch.Size([2947, 561]), y_val: torch.Size([2947])


/tmp/ipykernel_680917/323715209.py:48: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  checkpoint = torch.load(teacher_checkpoint_path, map_location=device)



🔎 Similarity Scores:
New Class 0:
  - Existing Class 0: 0.7231
  - Existing Class 1: 0.2248
  - Existing Class 2: 0.4900
  - Existing Class 3: 0.4209
New Class 1:
  - Existing Class 0: 0.3882
  - Existing Class 1: 0.7265
  - Existing Class 2: 0.6204
  - Existing Class 3: 0.3614
New Class 2:
  - Existing Class 0: 0.3990
  - Existing Class 1: 0.4850
  - Existing Class 2: 0.7458
  - Existing Class 3: 0.3074
New Class 3:
  - Existing Class 0: 0.6885
  - Existing Class 1: 0.3134
  - Existing Class 2: 0.3569
  - Existing Class 3: 0.7553
New Class 4:
  - Existing Class 0: 0.4633
  - Existing Class 1: 0.5467
  - Existing Class 2: 0.6458
  - Existing Class 3: 0.4990
New Class 5:
  - Existing Class 0: 0.4469
  - Existing Class 1: 0.4871
  - Existing Class 2: 0.7383
  - Existing Class 3: 0.4185
📊 Average similarity: 0.5105, Std: 0.1557
🧩 Similarity threshold: 0.5
👥 Existing classes: [0, 1, 2, 3]
🆕 New classes: [0, 1, 2, 3, 4, 5]
🧩 New classes detected (for LoRA decision): [4, 5]
[Similarity] Cla

## __~~~ ALL Test ~~~__

## __HAR_MLP_v2 Training (alpha = 0.1, similarity_threshold = 0.5)__

In [16]:
similarity_threshold=0.5

---
### Period 1 (alpha = 0.1, similarity_threshold = 0.5)
+ ##### Total training time: 149.73 seconds
+ ##### Model: HAR_MLP_LoRA_v2
+ ##### Training and saving in *'Class_Incremental_CL/HAR_CIL/Trained_models/DynEx_CLoRA/alpha_0.1/sim_thd_0.5/Period_1'*
+ ##### Best Epoch: 522
#### __Val Accuracy: 95.01%__
#### __Val-Class-Acc: {0: '92.67%', 1: '97.18%'}__

In [57]:
# ================================
# 📌 Period 1 Configuration - HAR_MLP_LoRA_v2
# ================================
period = 1

# Load dataset for this period
X_train, y_train = period_datasets[period]["train"]
X_val, y_val     = period_datasets[period]["test"]

# Auto-select CUDA device
device = auto_select_cuda_device()

# Model and training hyperparameters
input_size    = X_train.shape[1]
hidden_size   = 128
output_size   = len(set(y_train))
dropout       = 0.2
learning_rate = 0.0001
weight_decay  = 1e-5
num_epochs    = 1000
alpha         = 0.1  # Not used in Period 1 but passed for compatibility
teacher_model = None
stable_classes = None

# Model saving path
model_name = "HAR_MLP_LoRA_v2"
model_saving_folder = os.path.join(
    "Class_Incremental_CL", "HAR_CIL", "Trained_models", 
    "DynEx_CLoRA", f"alpha_{alpha}", f"sim_thd_{similarity_threshold}", f"Period_{period}"
)
os.makedirs(model_saving_folder, exist_ok=True)

# Initialize model, criterion, optimizer
student_model = HAR_MLP_LoRA_v2(
    input_size=input_size,
    hidden_size=hidden_size,
    output_size=output_size,
    dropout=dropout,
    lora_rank=4  # or whatever value you want
).to(device)

criterion = nn.CrossEntropyLoss()
optimizer = torch.optim.Adam(student_model.parameters(), lr=learning_rate, weight_decay=weight_decay)
scheduler = None

# Train the model
train_with_dynex_clora(
    model=student_model,
    teacher_model=teacher_model,
    output_size=output_size,
    criterion=criterion,
    optimizer=optimizer,
    X_train=X_train,
    y_train=y_train,
    X_val=X_val,
    y_val=y_val,
    num_epochs=num_epochs,
    batch_size=batch_size,
    alpha=alpha,
    model_saving_folder=model_saving_folder,
    model_name=model_name,
    stop_signal_file=stop_signal_file,
    scheduler=scheduler,
    period=period,
    stable_classes=stable_classes,
    class_features_dict=None,
    related_labels={"fc2": [0, 1]},  # Period 1 的初始化
    similarity_threshold=similarity_threshold
)

# ================================
# ✅ Summary & Resource Cleanup
# ================================
unique_classes = np.unique(y_train)
num_classes = len(unique_classes)

print(f"\n✅ Period {period} Training Complete. Final model architecture:")
print(student_model)
print(f"📊 Class Summary → unique_classes = {unique_classes}, num_classes = {num_classes}")

del X_train, y_train, X_val, y_val, teacher_model, student_model
gc.collect()
torch.cuda.empty_cache()


🎯 Automatically selected GPU:
    - CUDA Device ID : 0
    - Memory Used    : 18826 MiB
    - Device Name    : NVIDIA RTX A6000

🚀 'train_with_dynex_clora' started for Period 1

✅ Removed existing folder: Class_Incremental_CL/HAR_CIL/Trained_models/DynEx_CLoRA/alpha_0.1/sim_thd_0.5/Period_1
🎯 Automatically selected GPU:
    - CUDA Device ID : 0
    - Memory Used    : 18828 MiB
    - Device Name    : NVIDIA RTX A6000

✅ Data Overview:
X_train: torch.Size([2660, 561]), y_train: torch.Size([2660])
X_val: torch.Size([1023, 561]), y_val: torch.Size([1023])

📐 Model Architecture:
HAR_MLP_LoRA_v2(
  (fc1): Linear(in_features=561, out_features=128, bias=True)
  (bn1): BatchNorm1d(128, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  (relu1): ReLU()
  (dropout1): Dropout(p=0.2, inplace=False)
  (fc2): Linear(in_features=128, out_features=128, bias=True)
  (lora_adapters): ModuleList()
  (bn2): BatchNorm1d(128, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  (r

---
### Period 2 (alpha = 0.1, similarity_threshold = 0.5)
+ ##### Total training time: 435.67 seconds
+ ##### Model: HAR_MLP_LoRA_v2
+ ##### Training and saving in *'Class_Incremental_CL/HAR_CIL/Trained_models/DynEx_CLoRA/alpha_0.1/sim_thd_0.5/Period_2'*
+ ##### Best Epoch: 323
#### __Val Accuracy: 97.80%__
#### __Val-Class-Acc: {0: '92.46%', 1: '96.99%', 2: '100.00%'}__

In [19]:
# ================================
# 📌 Period 2 Configuration - HAR_MLP_LoRA_v2
# ================================
period = 2

X_train, y_train = period_datasets[period]["train"]
X_val, y_val     = period_datasets[period]["test"]

device = auto_select_cuda_device()

input_size    = X_train.shape[1]
hidden_size   = 128
output_size   = len(set(y_train))
dropout       = 0.2
learning_rate = 0.0001
weight_decay  = 1e-5
num_epochs    = 1000
alpha         = 0.1
stable_classes = [0, 1]  # 根據 Period 1 類別定義

model_name = "HAR_MLP_LoRA_v2"
model_saving_folder = os.path.join(
    "Class_Incremental_CL", "HAR_CIL", "Trained_models", 
    "DynEx_CLoRA", f"alpha_{alpha}", f"sim_thd_{similarity_threshold}", f"Period_{period}"
)
os.makedirs(model_saving_folder, exist_ok=True)

# Load previous class features
prev_folder = os.path.join(
    "Class_Incremental_CL", "HAR_CIL", "Trained_models", 
    "DynEx_CLoRA", f"alpha_{alpha}", f"sim_thd_{similarity_threshold}", f"Period_{period - 1}"
)
class_features_path = os.path.join(prev_folder, "class_features.pkl")
if os.path.exists(class_features_path):
    with open(class_features_path, 'rb') as f:
        class_features_dict = pickle.load(f)
    print(f"✅ Loaded class features from: {class_features_path}")
else:
    class_features_dict = {}
    print("⚠️ No previous class features found.")

# Load previous model as teacher
teacher_checkpoint_path = os.path.join(prev_folder, f"{model_name}_best.pth")
teacher_model = HAR_MLP_LoRA_v2(
    input_size=input_size,
    hidden_size=hidden_size,
    output_size=output_size - 1,  # Exclude new class
    dropout=dropout,
    lora_rank=4
).to(device)

checkpoint = torch.load(teacher_checkpoint_path, map_location=device)
num_lora_adapters = checkpoint.get("num_lora_adapters", 0)
print(f"Teacher model num_lora_adapters: {num_lora_adapters}")
related_labels = checkpoint.get("related_labels", {"fc2": [0, 1]})
print(f"Teacher checkpoint has {num_lora_adapters} LoRA adapters.")

for _ in range(num_lora_adapters):
    teacher_model.add_lora_adapter()
teacher_model.load_state_dict(checkpoint["model_state_dict"])
del checkpoint

# Instantiate student and initialize from teacher (except fc3)
student_model = HAR_MLP_LoRA_v2(
    input_size=input_size,
    hidden_size=hidden_size,
    output_size=output_size,
    dropout=dropout,
    lora_rank=4
).to(device)

for _ in range(num_lora_adapters):
    student_model.add_lora_adapter()

# Copy shared weights
teacher_dict = teacher_model.state_dict()
student_dict = student_model.state_dict()
for name, param in teacher_dict.items():
    if not name.startswith("fc3"):
        student_dict[name].copy_(param)
student_model.load_state_dict(student_dict)

# Train setup
criterion = nn.CrossEntropyLoss()
optimizer = torch.optim.Adam(student_model.parameters(), lr=learning_rate, weight_decay=weight_decay)
scheduler = None

# Train
train_with_dynex_clora(
    model=student_model,
    teacher_model=teacher_model,
    output_size=output_size,
    criterion=criterion,
    optimizer=optimizer,
    X_train=X_train,
    y_train=y_train,
    X_val=X_val,
    y_val=y_val,
    num_epochs=num_epochs,
    batch_size=batch_size,
    alpha=alpha,
    model_saving_folder=model_saving_folder,
    model_name=model_name,
    stop_signal_file=stop_signal_file,
    scheduler=scheduler,
    period=period,
    stable_classes=stable_classes,
    class_features_dict=class_features_dict,
    related_labels=related_labels,
    logic_version="all",  # or "all"
    similarity_threshold=similarity_threshold
)

# Cleanup
unique_classes = np.unique(y_train)
print(f"\nstudent_model summary:\n{student_model}")
print(f"unique_classes = {unique_classes}, num_classes = {len(unique_classes)}")

del X_train, y_train, X_val, y_val, teacher_model, student_model, teacher_dict, student_dict, teacher_checkpoint_path
gc.collect()
torch.cuda.empty_cache()


🎯 Automatically selected GPU:
    - CUDA Device ID : 0
    - Memory Used    : 4804 MiB
    - Device Name    : NVIDIA RTX A6000
✅ Loaded class features from: Class_Incremental_CL/HAR_CIL/Trained_models/DynEx_CLoRA/alpha_0.1/sim_thd_0.5/Period_1/class_features.pkl
Teacher model num_lora_adapters: 0
Teacher checkpoint has 0 LoRA adapters.

🚀 'train_with_dynex_clora' started for Period 2

✅ Removed existing folder: Class_Incremental_CL/HAR_CIL/Trained_models/DynEx_CLoRA/alpha_0.1/sim_thd_0.5/Period_2
🎯 Automatically selected GPU:
    - CUDA Device ID : 0
    - Memory Used    : 4806 MiB
    - Device Name    : NVIDIA RTX A6000


/tmp/ipykernel_2214128/18411275.py:52: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  checkpoint = torch.load(teacher_checkpoint_path, map_location=device)



✅ Data Overview:
X_train: torch.Size([5945, 561]), y_train: torch.Size([5945])
X_val: torch.Size([2410, 561]), y_val: torch.Size([2410])

🔎 Similarity Scores:
New Class 0:
  - Existing Class 0: 0.5012
  - Existing Class 1: 0.4951
New Class 1:
  - Existing Class 0: 0.4676
  - Existing Class 1: 0.4688
New Class 2:
  - Existing Class 0: 0.2119
  - Existing Class 1: 0.2032
📊 Average similarity: 0.3913, Std: 0.1306
🧩 Similarity threshold: 0.5
👥 Existing classes: [0, 1]
🆕 New classes: [0, 1, 2]
🧩 New classes detected (for LoRA decision): [2]
✅ Added LoRA adapter to HAR_MLP_LoRA_v2 (fc2), total adapters: 1
[Stability Check] Class 0 similarity with itself: 0.5012
[Stability Check] Class 1 similarity with itself: 0.4688
⚠️ Unfreezing fc2 due to low self-similarity of Class 1

📌 related_labels (after logic): {'fc2': [0, 1], 0: [2]}
📌 to_unfreeze set: {'fc2'}
📌 new_lora_indices: [0]

📐 Model Architecture:
HAR_MLP_LoRA_v2(
  (fc1): Linear(in_features=561, out_features=128, bias=True)
  (bn1): Bat

---
### Period 3 (alpha = 0.1, similarity_threshold = 0.5)
+ ##### Total training time: 513.51 seconds
+ ##### Model: HAR_MLP_LoRA_v2
+ ##### Training and saving in *'Class_Incremental_CL/HAR_CIL/Trained_models/DynEx_CLoRA/alpha_0.1/sim_thd_0.5/Period_3'*
+ ##### Best Epoch: 906
#### __Val Accuracy: 98.30%__
#### __Val-Class-Acc: {0: '93.69%', 1: '96.43%', 3: '100.00%', 2: '100.00%'}__

In [59]:
# ================================
# 📌 Period 3 Configuration - HAR_MLP_LoRA_v2
# ================================
period = 3

X_train, y_train = period_datasets[period]["train"]
X_val, y_val     = period_datasets[period]["test"]

input_size    = X_train.shape[1]
hidden_size   = 128
output_size   = len(set(y_train))
dropout       = 0.2
learning_rate = 0.0001
weight_decay  = 1e-5
num_epochs    = 1000
alpha         = 0.1
stable_classes = [0, 1, 2]

model_name = "HAR_MLP_LoRA_v2"
model_saving_folder = os.path.join(
    "Class_Incremental_CL", "HAR_CIL", "Trained_models", 
    "DynEx_CLoRA", f"alpha_{alpha}", f"sim_thd_{similarity_threshold}", f"Period_{period}"
)
os.makedirs(model_saving_folder, exist_ok=True)

prev_folder = os.path.join(
    "Class_Incremental_CL", "HAR_CIL", "Trained_models", 
    "DynEx_CLoRA", f"alpha_{alpha}", f"sim_thd_{similarity_threshold}", f"Period_{period - 1}"
)
class_features_path = os.path.join(prev_folder, "class_features.pkl")
if os.path.exists(class_features_path):
    with open(class_features_path, 'rb') as f:
        class_features_dict = pickle.load(f)
    print(f"✅ Loaded class features from: {class_features_path}")
else:
    class_features_dict = {}
    print("⚠️ No previous class features found.")

teacher_checkpoint_path = os.path.join(prev_folder, f"{model_name}_best.pth")
teacher_model = HAR_MLP_LoRA_v2(
    input_size=input_size,
    hidden_size=hidden_size,
    output_size=output_size - 1,
    dropout=dropout,
    lora_rank=4
).to(device)

checkpoint = torch.load(teacher_checkpoint_path, map_location=device)
num_lora_adapters = checkpoint.get("num_lora_adapters", 0)
related_labels = checkpoint.get("related_labels", {"fc2": [0, 1]})
for _ in range(num_lora_adapters):
    teacher_model.add_lora_adapter()
teacher_model.load_state_dict(checkpoint["model_state_dict"])
del checkpoint

student_model = HAR_MLP_LoRA_v2(
    input_size=input_size,
    hidden_size=hidden_size,
    output_size=output_size,
    dropout=dropout,
    lora_rank=4
).to(device)
for _ in range(num_lora_adapters):
    student_model.add_lora_adapter()

teacher_dict = teacher_model.state_dict()
student_dict = student_model.state_dict()
for name, param in teacher_dict.items():
    if not name.startswith("fc3"):
        student_dict[name].copy_(param)
student_model.load_state_dict(student_dict)

criterion = nn.CrossEntropyLoss()
optimizer = torch.optim.Adam(student_model.parameters(), lr=learning_rate, weight_decay=weight_decay)
scheduler = None

train_with_dynex_clora(
    model=student_model,
    teacher_model=teacher_model,
    output_size=output_size,
    criterion=criterion,
    optimizer=optimizer,
    X_train=X_train,
    y_train=y_train,
    X_val=X_val,
    y_val=y_val,
    num_epochs=num_epochs,
    batch_size=batch_size,
    alpha=alpha,
    model_saving_folder=model_saving_folder,
    model_name=model_name,
    stop_signal_file=stop_signal_file,
    scheduler=scheduler,
    period=period,
    stable_classes=stable_classes,
    class_features_dict=class_features_dict,
    related_labels=related_labels,
    logic_version="all",
    similarity_threshold=similarity_threshold
)

unique_classes = np.unique(y_train)
print(f"\nstudent_model summary:\n{student_model}")
print(f"unique_classes = {unique_classes}, num_classes = {len(unique_classes)}")

del X_train, y_train, X_val, y_val, teacher_model, student_model, teacher_dict, student_dict, teacher_checkpoint_path
gc.collect()
torch.cuda.empty_cache()


✅ Loaded class features from: Class_Incremental_CL/HAR_CIL/Trained_models/DynEx_CLoRA/alpha_0.1/sim_thd_0.5/Period_2/class_features.pkl
✅ Added LoRA adapter to HAR_MLP_LoRA_v2 (fc2), total adapters: 1
✅ Added LoRA adapter to HAR_MLP_LoRA_v2 (fc2), total adapters: 1

🚀 'train_with_dynex_clora' started for Period 3

✅ Removed existing folder: Class_Incremental_CL/HAR_CIL/Trained_models/DynEx_CLoRA/alpha_0.1/sim_thd_0.5/Period_3
🎯 Automatically selected GPU:
    - CUDA Device ID : 2
    - Memory Used    : 741 MiB
    - Device Name    : NVIDIA RTX A6000


/tmp/ipykernel_680917/2042533669.py:48: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  checkpoint = torch.load(teacher_checkpoint_path, map_location=device)



✅ Data Overview:
X_train: torch.Size([7352, 561]), y_train: torch.Size([7352])
X_val: torch.Size([2947, 561]), y_val: torch.Size([2947])

🔎 Similarity Scores:
New Class 0:
  - Existing Class 0: 0.8474
  - Existing Class 1: 0.3617
  - Existing Class 2: 0.4122
New Class 1:
  - Existing Class 0: 0.5238
  - Existing Class 1: 0.6342
  - Existing Class 2: 0.2276
New Class 2:
  - Existing Class 0: 0.6987
  - Existing Class 1: 0.8143
  - Existing Class 2: 0.6468
New Class 3:
  - Existing Class 0: 0.6376
  - Existing Class 1: 0.4728
  - Existing Class 2: 0.2285
📊 Average similarity: 0.5421, Std: 0.1984
🧩 Similarity threshold: 0.5
👥 Existing classes: [0, 1, 2]
🆕 New classes: [0, 1, 2, 3]
🧩 New classes detected (for LoRA decision): [3]
🔄 New Class 3 is similar to Old Class 0 (Sim=0.6376) → Associated with network 'fc2', related_labels[fc2] now: [0, 1, 3]
[Stability Check] Class 0 similarity with itself: 0.8474
[Stability Check] Class 1 similarity with itself: 0.6342
[Stability Check] Class 2 sim

---
### Period 4 (alpha = 0.1, similarity_threshold = 0.5)
+ ##### Total training time: 599.29 seconds
+ ##### Model: HAR_MLP_LoRA_v2
+ ##### Training and saving in *'Class_Incremental_CL/HAR_CIL/Trained_models/DynEx_CLoRA/alpha_0.1/sim_thd_0.5/Period_4'*
+ ##### Best Epoch: 863
#### __Val Accuracy: 97.49%__
#### __Val-Class-Acc: {0: '94.50%', 1: '95.30%', 3: '100.00%', 2: '99.80%', 5: '99.29%', 4: '96.18%'}__

In [60]:
# ================================
# 📌 Period 4 Configuration - HAR_MLP_LoRA_v2
# ================================
period = 4

X_train, y_train = period_datasets[period]["train"]
X_val, y_val     = period_datasets[period]["test"]

input_size    = X_train.shape[1]
hidden_size   = 128
output_size   = len(set(y_train))
dropout       = 0.2
learning_rate = 0.0001
weight_decay  = 1e-5
num_epochs    = 1000
alpha         = 0.1
stable_classes = [0, 1, 3]

model_name = "HAR_MLP_LoRA_v2"
model_saving_folder = os.path.join(
    "Class_Incremental_CL", "HAR_CIL", "Trained_models", 
    "DynEx_CLoRA", f"alpha_{alpha}", f"sim_thd_{similarity_threshold}", f"Period_{period}"
)
os.makedirs(model_saving_folder, exist_ok=True)

prev_folder = os.path.join(
    "Class_Incremental_CL", "HAR_CIL", "Trained_models", 
    "DynEx_CLoRA", f"alpha_{alpha}", f"sim_thd_{similarity_threshold}", f"Period_{period - 1}"
)
class_features_path = os.path.join(prev_folder, "class_features.pkl")
if os.path.exists(class_features_path):
    with open(class_features_path, 'rb') as f:
        class_features_dict = pickle.load(f)
    print(f"✅ Loaded class features from: {class_features_path}")
else:
    class_features_dict = {}
    print("⚠️ No previous class features found.")

teacher_checkpoint_path = os.path.join(prev_folder, f"{model_name}_best.pth")
teacher_model = HAR_MLP_LoRA_v2(
    input_size=input_size,
    hidden_size=hidden_size,
    output_size=output_size - 2,
    dropout=dropout,
    lora_rank=4
).to(device)

checkpoint = torch.load(teacher_checkpoint_path, map_location=device)
num_lora_adapters = checkpoint.get("num_lora_adapters", 0)
related_labels = checkpoint.get("related_labels", {"fc2": [0, 1]})
for _ in range(num_lora_adapters):
    teacher_model.add_lora_adapter()
teacher_model.load_state_dict(checkpoint["model_state_dict"])
del checkpoint

student_model = HAR_MLP_LoRA_v2(
    input_size=input_size,
    hidden_size=hidden_size,
    output_size=output_size,
    dropout=dropout,
    lora_rank=4
).to(device)
for _ in range(num_lora_adapters):
    student_model.add_lora_adapter()

teacher_dict = teacher_model.state_dict()
student_dict = student_model.state_dict()
for name, param in teacher_dict.items():
    if not name.startswith("fc3"):
        student_dict[name].copy_(param)
student_model.load_state_dict(student_dict)

criterion = nn.CrossEntropyLoss()
optimizer = torch.optim.Adam(student_model.parameters(), lr=learning_rate, weight_decay=weight_decay)
scheduler = None

train_with_dynex_clora(
    model=student_model,
    teacher_model=teacher_model,
    output_size=output_size,
    criterion=criterion,
    optimizer=optimizer,
    X_train=X_train,
    y_train=y_train,
    X_val=X_val,
    y_val=y_val,
    num_epochs=num_epochs,
    batch_size=batch_size,
    alpha=alpha,
    model_saving_folder=model_saving_folder,
    model_name=model_name,
    stop_signal_file=stop_signal_file,
    scheduler=scheduler,
    period=period,
    stable_classes=stable_classes,
    class_features_dict=class_features_dict,
    related_labels=related_labels,
    logic_version="all",
    similarity_threshold=similarity_threshold
)

unique_classes = np.unique(y_train)
print(f"\nstudent_model summary:\n{student_model}")
print(f"unique_classes = {unique_classes}, num_classes = {len(unique_classes)}")

del X_train, y_train, X_val, y_val, teacher_model, student_model, teacher_dict, student_dict, teacher_checkpoint_path
gc.collect()
torch.cuda.empty_cache()


✅ Loaded class features from: Class_Incremental_CL/HAR_CIL/Trained_models/DynEx_CLoRA/alpha_0.1/sim_thd_0.5/Period_3/class_features.pkl
✅ Added LoRA adapter to HAR_MLP_LoRA_v2 (fc2), total adapters: 1
✅ Added LoRA adapter to HAR_MLP_LoRA_v2 (fc2), total adapters: 1

🚀 'train_with_dynex_clora' started for Period 4

✅ Removed existing folder: Class_Incremental_CL/HAR_CIL/Trained_models/DynEx_CLoRA/alpha_0.1/sim_thd_0.5/Period_4
🎯 Automatically selected GPU:
    - CUDA Device ID : 0
    - Memory Used    : 771 MiB
    - Device Name    : NVIDIA RTX A6000

✅ Data Overview:
X_train: torch.Size([7352, 561]), y_train: torch.Size([7352])
X_val: torch.Size([2947, 561]), y_val: torch.Size([2947])


/tmp/ipykernel_680917/2955988379.py:48: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  checkpoint = torch.load(teacher_checkpoint_path, map_location=device)



🔎 Similarity Scores:
New Class 0:
  - Existing Class 0: 0.7694
  - Existing Class 1: 0.3042
  - Existing Class 2: 0.5425
  - Existing Class 3: 0.5041
New Class 1:
  - Existing Class 0: 0.3881
  - Existing Class 1: 0.6260
  - Existing Class 2: 0.4729
  - Existing Class 3: 0.2791
New Class 2:
  - Existing Class 0: 0.3668
  - Existing Class 1: 0.3182
  - Existing Class 2: 0.7612
  - Existing Class 3: 0.3801
New Class 3:
  - Existing Class 0: 0.4541
  - Existing Class 1: 0.3949
  - Existing Class 2: 0.5599
  - Existing Class 3: 0.5683
New Class 4:
  - Existing Class 0: 0.2667
  - Existing Class 1: 0.3232
  - Existing Class 2: 0.6579
  - Existing Class 3: 0.4035
New Class 5:
  - Existing Class 0: 0.3320
  - Existing Class 1: 0.3153
  - Existing Class 2: 0.7579
  - Existing Class 3: 0.3946
📊 Average similarity: 0.4642, Std: 0.1547
🧩 Similarity threshold: 0.5
👥 Existing classes: [0, 1, 2, 3]
🆕 New classes: [0, 1, 2, 3, 4, 5]
🧩 New classes detected (for LoRA decision): [4, 5]
🔄 New Class 4 is

## __HAR_MLP_v2 Training (alpha = 0.2, similarity_threshold = 0.5)__

In [61]:
similarity_threshold=0.5

---
### Period 1 (alpha = 0.2, similarity_threshold = 0.5)
+ ##### Total training time: 149.07 seconds
+ ##### Model: HAR_MLP_LoRA_v2
+ ##### Training and saving in *'Class_Incremental_CL/HAR_CIL/Trained_models/DynEx_CLoRA/alpha_0.2/sim_thd_0.5/Period_1'*
+ ##### Best Epoch: 801
#### __Val Accuracy: 95.31%__
#### __Val-Class-Acc: {0: '95.32%', 1: '95.30%'}__

In [62]:
# ================================
# 📌 Period 1 Configuration - HAR_MLP_LoRA_v2
# ================================
period = 1

# Load dataset for this period
X_train, y_train = period_datasets[period]["train"]
X_val, y_val     = period_datasets[period]["test"]

# Auto-select CUDA device
device = auto_select_cuda_device()

# Model and training hyperparameters
input_size    = X_train.shape[1]
hidden_size   = 128
output_size   = len(set(y_train))
dropout       = 0.2
learning_rate = 0.0001
weight_decay  = 1e-5
num_epochs    = 1000
alpha         = 0.2  # Not used in Period 1 but passed for compatibility
teacher_model = None
stable_classes = None

# Model saving path
model_name = "HAR_MLP_LoRA_v2"
model_saving_folder = os.path.join(
    "Class_Incremental_CL", "HAR_CIL", "Trained_models", 
    "DynEx_CLoRA", f"alpha_{alpha}", f"sim_thd_{similarity_threshold}", f"Period_{period}"
)
os.makedirs(model_saving_folder, exist_ok=True)

# Initialize model, criterion, optimizer
student_model = HAR_MLP_LoRA_v2(
    input_size=input_size,
    hidden_size=hidden_size,
    output_size=output_size,
    dropout=dropout,
    lora_rank=4  # or whatever value you want
).to(device)

criterion = nn.CrossEntropyLoss()
optimizer = torch.optim.Adam(student_model.parameters(), lr=learning_rate, weight_decay=weight_decay)
scheduler = None

# Train the model
train_with_dynex_clora(
    model=student_model,
    teacher_model=teacher_model,
    output_size=output_size,
    criterion=criterion,
    optimizer=optimizer,
    X_train=X_train,
    y_train=y_train,
    X_val=X_val,
    y_val=y_val,
    num_epochs=num_epochs,
    batch_size=batch_size,
    alpha=alpha,
    model_saving_folder=model_saving_folder,
    model_name=model_name,
    stop_signal_file=stop_signal_file,
    scheduler=scheduler,
    period=period,
    stable_classes=stable_classes,
    class_features_dict=None,
    related_labels={"fc2": [0, 1]},  # Period 1 的初始化
    similarity_threshold=similarity_threshold
)

# ================================
# ✅ Summary & Resource Cleanup
# ================================
unique_classes = np.unique(y_train)
num_classes = len(unique_classes)

print(f"\n✅ Period {period} Training Complete. Final model architecture:")
print(student_model)
print(f"📊 Class Summary → unique_classes = {unique_classes}, num_classes = {num_classes}")

del X_train, y_train, X_val, y_val, teacher_model, student_model
gc.collect()
torch.cuda.empty_cache()


🎯 Automatically selected GPU:
    - CUDA Device ID : 0
    - Memory Used    : 775 MiB
    - Device Name    : NVIDIA RTX A6000

🚀 'train_with_dynex_clora' started for Period 1

✅ Removed existing folder: Class_Incremental_CL/HAR_CIL/Trained_models/DynEx_CLoRA/alpha_0.2/sim_thd_0.5/Period_1
🎯 Automatically selected GPU:
    - CUDA Device ID : 0
    - Memory Used    : 775 MiB
    - Device Name    : NVIDIA RTX A6000

✅ Data Overview:
X_train: torch.Size([2660, 561]), y_train: torch.Size([2660])
X_val: torch.Size([1023, 561]), y_val: torch.Size([1023])

📐 Model Architecture:
HAR_MLP_LoRA_v2(
  (fc1): Linear(in_features=561, out_features=128, bias=True)
  (bn1): BatchNorm1d(128, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  (relu1): ReLU()
  (dropout1): Dropout(p=0.2, inplace=False)
  (fc2): Linear(in_features=128, out_features=128, bias=True)
  (lora_adapters): ModuleList()
  (bn2): BatchNorm1d(128, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  (relu2

---
### Period 2 (alpha = 0.2, similarity_threshold = 0.5)
+ ##### Total training time: 436.89 seconds
+ ##### Model: HAR_MLP_LoRA_v2
+ ##### Training and saving in *'Class_Incremental_CL/HAR_CIL/Trained_models/DynEx_CLoRA/alpha_0.2/sim_thd_0.5/Period_2'*
+ ##### Best Epoch: 189
#### __Val Accuracy: 98.05%__
#### __Val-Class-Acc: {0: '92.87%', 1: '97.74%', 2: '100.00%'}__

In [63]:
# ================================
# 📌 Period 2 Configuration - HAR_MLP_LoRA_v2
# ================================
period = 2

X_train, y_train = period_datasets[period]["train"]
X_val, y_val     = period_datasets[period]["test"]

device = auto_select_cuda_device()

input_size    = X_train.shape[1]
hidden_size   = 128
output_size   = len(set(y_train))
dropout       = 0.2
learning_rate = 0.0001
weight_decay  = 1e-5
num_epochs    = 1000
alpha         = 0.2
stable_classes = [0, 1]  # 根據 Period 1 類別定義

model_name = "HAR_MLP_LoRA_v2"
model_saving_folder = os.path.join(
    "Class_Incremental_CL", "HAR_CIL", "Trained_models", 
    "DynEx_CLoRA", f"alpha_{alpha}", f"sim_thd_{similarity_threshold}", f"Period_{period}"
)
os.makedirs(model_saving_folder, exist_ok=True)

# Load previous class features
prev_folder = os.path.join(
    "Class_Incremental_CL", "HAR_CIL", "Trained_models", 
    "DynEx_CLoRA", f"alpha_{alpha}", f"sim_thd_{similarity_threshold}", f"Period_{period - 1}"
)
class_features_path = os.path.join(prev_folder, "class_features.pkl")
if os.path.exists(class_features_path):
    with open(class_features_path, 'rb') as f:
        class_features_dict = pickle.load(f)
    print(f"✅ Loaded class features from: {class_features_path}")
else:
    class_features_dict = {}
    print("⚠️ No previous class features found.")

# Load previous model as teacher
teacher_checkpoint_path = os.path.join(prev_folder, f"{model_name}_best.pth")
teacher_model = HAR_MLP_LoRA_v2(
    input_size=input_size,
    hidden_size=hidden_size,
    output_size=output_size - 1,  # Exclude new class
    dropout=dropout,
    lora_rank=4
).to(device)

checkpoint = torch.load(teacher_checkpoint_path, map_location=device)
num_lora_adapters = checkpoint.get("num_lora_adapters", 0)
print(f"Teacher model num_lora_adapters: {num_lora_adapters}")
related_labels = checkpoint.get("related_labels", {"fc2": [0, 1]})
print(f"Teacher checkpoint has {num_lora_adapters} LoRA adapters.")

for _ in range(num_lora_adapters):
    teacher_model.add_lora_adapter()
teacher_model.load_state_dict(checkpoint["model_state_dict"])
del checkpoint

# Instantiate student and initialize from teacher (except fc3)
student_model = HAR_MLP_LoRA_v2(
    input_size=input_size,
    hidden_size=hidden_size,
    output_size=output_size,
    dropout=dropout,
    lora_rank=4
).to(device)

for _ in range(num_lora_adapters):
    student_model.add_lora_adapter()

# Copy shared weights
teacher_dict = teacher_model.state_dict()
student_dict = student_model.state_dict()
for name, param in teacher_dict.items():
    if not name.startswith("fc3"):
        student_dict[name].copy_(param)
student_model.load_state_dict(student_dict)

# Train setup
criterion = nn.CrossEntropyLoss()
optimizer = torch.optim.Adam(student_model.parameters(), lr=learning_rate, weight_decay=weight_decay)
scheduler = None

# Train
train_with_dynex_clora(
    model=student_model,
    teacher_model=teacher_model,
    output_size=output_size,
    criterion=criterion,
    optimizer=optimizer,
    X_train=X_train,
    y_train=y_train,
    X_val=X_val,
    y_val=y_val,
    num_epochs=num_epochs,
    batch_size=batch_size,
    alpha=alpha,
    model_saving_folder=model_saving_folder,
    model_name=model_name,
    stop_signal_file=stop_signal_file,
    scheduler=scheduler,
    period=period,
    stable_classes=stable_classes,
    class_features_dict=class_features_dict,
    related_labels=related_labels,
    logic_version="all",  # or "all"
    similarity_threshold=similarity_threshold
)

# Cleanup
unique_classes = np.unique(y_train)
print(f"\nstudent_model summary:\n{student_model}")
print(f"unique_classes = {unique_classes}, num_classes = {len(unique_classes)}")

del X_train, y_train, X_val, y_val, teacher_model, student_model, teacher_dict, student_dict, teacher_checkpoint_path
gc.collect()
torch.cuda.empty_cache()


🎯 Automatically selected GPU:
    - CUDA Device ID : 0
    - Memory Used    : 775 MiB
    - Device Name    : NVIDIA RTX A6000
✅ Loaded class features from: Class_Incremental_CL/HAR_CIL/Trained_models/DynEx_CLoRA/alpha_0.2/sim_thd_0.5/Period_1/class_features.pkl
Teacher model num_lora_adapters: 0
Teacher checkpoint has 0 LoRA adapters.

🚀 'train_with_dynex_clora' started for Period 2

✅ Removed existing folder: Class_Incremental_CL/HAR_CIL/Trained_models/DynEx_CLoRA/alpha_0.2/sim_thd_0.5/Period_2
🎯 Automatically selected GPU:
    - CUDA Device ID : 0
    - Memory Used    : 775 MiB
    - Device Name    : NVIDIA RTX A6000

✅ Data Overview:
X_train: torch.Size([5945, 561]), y_train: torch.Size([5945])
X_val: torch.Size([2410, 561]), y_val: torch.Size([2410])


/tmp/ipykernel_680917/594361794.py:52: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  checkpoint = torch.load(teacher_checkpoint_path, map_location=device)



🔎 Similarity Scores:
New Class 0:
  - Existing Class 0: 0.4841
  - Existing Class 1: 0.4753
New Class 1:
  - Existing Class 0: 0.5763
  - Existing Class 1: 0.5859
New Class 2:
  - Existing Class 0: 0.2648
  - Existing Class 1: 0.2630
📊 Average similarity: 0.4416, Std: 0.1323
🧩 Similarity threshold: 0.5
👥 Existing classes: [0, 1]
🆕 New classes: [0, 1, 2]
🧩 New classes detected (for LoRA decision): [2]
✅ Added LoRA adapter to HAR_MLP_LoRA_v2 (fc2), total adapters: 1
[Stability Check] Class 0 similarity with itself: 0.4841
⚠️ Unfreezing fc2 due to low self-similarity of Class 0
[Stability Check] Class 1 similarity with itself: 0.5859

📌 related_labels (after logic): {'fc2': [0, 1], 0: [2]}
📌 to_unfreeze set: {'fc2'}
📌 new_lora_indices: [0]

📐 Model Architecture:
HAR_MLP_LoRA_v2(
  (fc1): Linear(in_features=561, out_features=128, bias=True)
  (bn1): BatchNorm1d(128, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  (relu1): ReLU()
  (dropout1): Dropout(p=0.2, inplace=False

---
### Period 3 (alpha = 0.2, similarity_threshold = 0.5)
+ ##### Total training time: 609.50 seconds
+ ##### Model: HAR_MLP_LoRA_v2
+ ##### Training and saving in *'Class_Incremental_CL/HAR_CIL/Trained_models/DynEx_CLoRA/alpha_0.2/sim_thd_0.5/Period_3'*
+ ##### Best Epoch: 638
#### __Val Accuracy: 98.24%__
#### __Val-Class-Acc: {0: '93.48%', 1: '96.24%', 3: '100.00%', 2: '100.00%'}__

In [17]:
# ================================
# 📌 Period 3 Configuration - HAR_MLP_LoRA_v2
# ================================
period = 3

X_train, y_train = period_datasets[period]["train"]
X_val, y_val     = period_datasets[period]["test"]

input_size    = X_train.shape[1]
hidden_size   = 128
output_size   = len(set(y_train))
dropout       = 0.2
learning_rate = 0.0001
weight_decay  = 1e-5
num_epochs    = 1000
alpha         = 0.2
stable_classes = [0, 1, 2]

model_name = "HAR_MLP_LoRA_v2"
model_saving_folder = os.path.join(
    "Class_Incremental_CL", "HAR_CIL", "Trained_models", 
    "DynEx_CLoRA", f"alpha_{alpha}", f"sim_thd_{similarity_threshold}", f"Period_{period}"
)
os.makedirs(model_saving_folder, exist_ok=True)

prev_folder = os.path.join(
    "Class_Incremental_CL", "HAR_CIL", "Trained_models", 
    "DynEx_CLoRA", f"alpha_{alpha}", f"sim_thd_{similarity_threshold}", f"Period_{period - 1}"
)
class_features_path = os.path.join(prev_folder, "class_features.pkl")
if os.path.exists(class_features_path):
    with open(class_features_path, 'rb') as f:
        class_features_dict = pickle.load(f)
    print(f"✅ Loaded class features from: {class_features_path}")
else:
    class_features_dict = {}
    print("⚠️ No previous class features found.")

teacher_checkpoint_path = os.path.join(prev_folder, f"{model_name}_best.pth")
teacher_model = HAR_MLP_LoRA_v2(
    input_size=input_size,
    hidden_size=hidden_size,
    output_size=output_size - 1,
    dropout=dropout,
    lora_rank=4
).to(device)

checkpoint = torch.load(teacher_checkpoint_path, map_location=device)
num_lora_adapters = checkpoint.get("num_lora_adapters", 0)
related_labels = checkpoint.get("related_labels", {"fc2": [0, 1]})
for _ in range(num_lora_adapters):
    teacher_model.add_lora_adapter()
teacher_model.load_state_dict(checkpoint["model_state_dict"])
del checkpoint

student_model = HAR_MLP_LoRA_v2(
    input_size=input_size,
    hidden_size=hidden_size,
    output_size=output_size,
    dropout=dropout,
    lora_rank=4
).to(device)
for _ in range(num_lora_adapters):
    student_model.add_lora_adapter()

teacher_dict = teacher_model.state_dict()
student_dict = student_model.state_dict()
for name, param in teacher_dict.items():
    if not name.startswith("fc3"):
        student_dict[name].copy_(param)
student_model.load_state_dict(student_dict)

criterion = nn.CrossEntropyLoss()
optimizer = torch.optim.Adam(student_model.parameters(), lr=learning_rate, weight_decay=weight_decay)
scheduler = None

train_with_dynex_clora(
    model=student_model,
    teacher_model=teacher_model,
    output_size=output_size,
    criterion=criterion,
    optimizer=optimizer,
    X_train=X_train,
    y_train=y_train,
    X_val=X_val,
    y_val=y_val,
    num_epochs=num_epochs,
    batch_size=batch_size,
    alpha=alpha,
    model_saving_folder=model_saving_folder,
    model_name=model_name,
    stop_signal_file=stop_signal_file,
    scheduler=scheduler,
    period=period,
    stable_classes=stable_classes,
    class_features_dict=class_features_dict,
    related_labels=related_labels,
    logic_version="all",
    similarity_threshold=similarity_threshold
)

unique_classes = np.unique(y_train)
print(f"\nstudent_model summary:\n{student_model}")
print(f"unique_classes = {unique_classes}, num_classes = {len(unique_classes)}")

del X_train, y_train, X_val, y_val, teacher_model, student_model, teacher_dict, student_dict, teacher_checkpoint_path
gc.collect()
torch.cuda.empty_cache()


✅ Loaded class features from: Class_Incremental_CL/HAR_CIL/Trained_models/DynEx_CLoRA/alpha_0.2/sim_thd_0.5/Period_2/class_features.pkl


/tmp/ipykernel_2214128/3996537997.py:48: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  checkpoint = torch.load(teacher_checkpoint_path, map_location=device)


✅ Added LoRA adapter to HAR_MLP_LoRA_v2 (fc2), total adapters: 1
✅ Added LoRA adapter to HAR_MLP_LoRA_v2 (fc2), total adapters: 1

🚀 'train_with_dynex_clora' started for Period 3

✅ Removed existing folder: Class_Incremental_CL/HAR_CIL/Trained_models/DynEx_CLoRA/alpha_0.2/sim_thd_0.5/Period_3
🎯 Automatically selected GPU:
    - CUDA Device ID : 2
    - Memory Used    : 20871 MiB
    - Device Name    : NVIDIA RTX A6000

✅ Data Overview:
X_train: torch.Size([7352, 561]), y_train: torch.Size([7352])
X_val: torch.Size([2947, 561]), y_val: torch.Size([2947])

🔎 Similarity Scores:
New Class 0:
  - Existing Class 0: 0.7520
  - Existing Class 1: 0.4368
  - Existing Class 2: 0.2371
New Class 1:
  - Existing Class 0: 0.4960
  - Existing Class 1: 0.6892
  - Existing Class 2: 0.2387
New Class 2:
  - Existing Class 0: 0.6823
  - Existing Class 1: 0.7540
  - Existing Class 2: 0.5531
New Class 3:
  - Existing Class 0: 0.4596
  - Existing Class 1: 0.4826
  - Existing Class 2: 0.1635
📊 Average similari

---
### Period 4 (alpha = 0.2, similarity_threshold = 0.5)
+ ##### Total training time: 1537.80 seconds
+ ##### Model: HAR_MLP_LoRA_v2
+ ##### Training and saving in *'Class_Incremental_CL/HAR_CIL/Trained_models/DynEx_CLoRA/alpha_0.2/sim_thd_0.5/Period_4'*
+ ##### Best Epoch: 970
#### __Val Accuracy: 96.54%__
#### __Val-Class-Acc: {0: '92.46%', 1: '96.05%', 3: '100.00%', 2: '99.80%', 5: '97.62%', 4: '92.99%'}__

In [18]:
# ================================
# 📌 Period 4 Configuration - HAR_MLP_LoRA_v2
# ================================
period = 4

X_train, y_train = period_datasets[period]["train"]
X_val, y_val     = period_datasets[period]["test"]

input_size    = X_train.shape[1]
hidden_size   = 128
output_size   = len(set(y_train))
dropout       = 0.2
learning_rate = 0.0001
weight_decay  = 1e-5
num_epochs    = 1000
alpha         = 0.2
stable_classes = [0, 1, 3]

model_name = "HAR_MLP_LoRA_v2"
model_saving_folder = os.path.join(
    "Class_Incremental_CL", "HAR_CIL", "Trained_models", 
    "DynEx_CLoRA", f"alpha_{alpha}", f"sim_thd_{similarity_threshold}", f"Period_{period}"
)
os.makedirs(model_saving_folder, exist_ok=True)

prev_folder = os.path.join(
    "Class_Incremental_CL", "HAR_CIL", "Trained_models", 
    "DynEx_CLoRA", f"alpha_{alpha}", f"sim_thd_{similarity_threshold}", f"Period_{period - 1}"
)
class_features_path = os.path.join(prev_folder, "class_features.pkl")
if os.path.exists(class_features_path):
    with open(class_features_path, 'rb') as f:
        class_features_dict = pickle.load(f)
    print(f"✅ Loaded class features from: {class_features_path}")
else:
    class_features_dict = {}
    print("⚠️ No previous class features found.")

teacher_checkpoint_path = os.path.join(prev_folder, f"{model_name}_best.pth")
teacher_model = HAR_MLP_LoRA_v2(
    input_size=input_size,
    hidden_size=hidden_size,
    output_size=output_size - 2,
    dropout=dropout,
    lora_rank=4
).to(device)

checkpoint = torch.load(teacher_checkpoint_path, map_location=device)
num_lora_adapters = checkpoint.get("num_lora_adapters", 0)
related_labels = checkpoint.get("related_labels", {"fc2": [0, 1]})
for _ in range(num_lora_adapters):
    teacher_model.add_lora_adapter()
teacher_model.load_state_dict(checkpoint["model_state_dict"])
del checkpoint

student_model = HAR_MLP_LoRA_v2(
    input_size=input_size,
    hidden_size=hidden_size,
    output_size=output_size,
    dropout=dropout,
    lora_rank=4
).to(device)
for _ in range(num_lora_adapters):
    student_model.add_lora_adapter()

teacher_dict = teacher_model.state_dict()
student_dict = student_model.state_dict()
for name, param in teacher_dict.items():
    if not name.startswith("fc3"):
        student_dict[name].copy_(param)
student_model.load_state_dict(student_dict)

criterion = nn.CrossEntropyLoss()
optimizer = torch.optim.Adam(student_model.parameters(), lr=learning_rate, weight_decay=weight_decay)
scheduler = None

train_with_dynex_clora(
    model=student_model,
    teacher_model=teacher_model,
    output_size=output_size,
    criterion=criterion,
    optimizer=optimizer,
    X_train=X_train,
    y_train=y_train,
    X_val=X_val,
    y_val=y_val,
    num_epochs=num_epochs,
    batch_size=batch_size,
    alpha=alpha,
    model_saving_folder=model_saving_folder,
    model_name=model_name,
    stop_signal_file=stop_signal_file,
    scheduler=scheduler,
    period=period,
    stable_classes=stable_classes,
    class_features_dict=class_features_dict,
    related_labels=related_labels,
    logic_version="all",
    similarity_threshold=similarity_threshold
)

unique_classes = np.unique(y_train)
print(f"\nstudent_model summary:\n{student_model}")
print(f"unique_classes = {unique_classes}, num_classes = {len(unique_classes)}")

del X_train, y_train, X_val, y_val, teacher_model, student_model, teacher_dict, student_dict, teacher_checkpoint_path
gc.collect()
torch.cuda.empty_cache()


✅ Loaded class features from: Class_Incremental_CL/HAR_CIL/Trained_models/DynEx_CLoRA/alpha_0.2/sim_thd_0.5/Period_3/class_features.pkl
✅ Added LoRA adapter to HAR_MLP_LoRA_v2 (fc2), total adapters: 1
✅ Added LoRA adapter to HAR_MLP_LoRA_v2 (fc2), total adapters: 2
✅ Added LoRA adapter to HAR_MLP_LoRA_v2 (fc2), total adapters: 1
✅ Added LoRA adapter to HAR_MLP_LoRA_v2 (fc2), total adapters: 2

🚀 'train_with_dynex_clora' started for Period 4

✅ Removed existing folder: Class_Incremental_CL/HAR_CIL/Trained_models/DynEx_CLoRA/alpha_0.2/sim_thd_0.5/Period_4
🎯 Automatically selected GPU:
    - CUDA Device ID : 2
    - Memory Used    : 19929 MiB
    - Device Name    : NVIDIA RTX A6000

✅ Data Overview:
X_train: torch.Size([7352, 561]), y_train: torch.Size([7352])
X_val: torch.Size([2947, 561]), y_val: torch.Size([2947])


/tmp/ipykernel_2214128/465567074.py:48: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  checkpoint = torch.load(teacher_checkpoint_path, map_location=device)



🔎 Similarity Scores:
New Class 0:
  - Existing Class 0: 0.7159
  - Existing Class 1: 0.3688
  - Existing Class 2: 0.4339
  - Existing Class 3: 0.4184
New Class 1:
  - Existing Class 0: 0.3968
  - Existing Class 1: 0.7560
  - Existing Class 2: 0.3998
  - Existing Class 3: 0.3110
New Class 2:
  - Existing Class 0: 0.4440
  - Existing Class 1: 0.4111
  - Existing Class 2: 0.8246
  - Existing Class 3: 0.3639
New Class 3:
  - Existing Class 0: 0.7583
  - Existing Class 1: 0.3649
  - Existing Class 2: 0.3793
  - Existing Class 3: 0.7081
New Class 4:
  - Existing Class 0: 0.4248
  - Existing Class 1: 0.4736
  - Existing Class 2: 0.7237
  - Existing Class 3: 0.4092
New Class 5:
  - Existing Class 0: 0.4459
  - Existing Class 1: 0.3634
  - Existing Class 2: 0.8150
  - Existing Class 3: 0.3468
📊 Average similarity: 0.5024, Std: 0.1688
🧩 Similarity threshold: 0.5
👥 Existing classes: [0, 1, 2, 3]
🆕 New classes: [0, 1, 2, 3, 4, 5]
🧩 New classes detected (for LoRA decision): [4, 5]
🔄 New Class 4 is

---

## 📊 Summary (init): 

### DynEx-CLoRA (Average Similarity Test, α = 0.1)

| Period | Training Time (s) | Validation Accuracy | Class-wise Accuracy                                                    |
|--------|-------------------|---------------------|-------------------------------------------------------------------------|
| 1      | 147.35            | **94.62%**          | {0: 91.45%, 1: 97.56%}                                                 |
| 2      | 416.32            | **97.72%**          | {0: 93.48%, 1: 95.68%, 2: 100.00%}                                     |
| 3      | 567.35            | **98.30%**          | {0: 94.30%, 1: 95.86%, 2: 100.00%, 3: 100.00%}                         |
| 4      | 582.08            | **97.15%**          | {0: 91.24%, 1: 97.18%, 2: 99.60%, 3: 100.00%, 4: 96.60%, 5: 98.10%}    |

### DynEx-CLoRA (Average Similarity Test, α = 0.2)

| Period | Training Time (s) | Validation Accuracy | Class-wise Accuracy                                                    |
|--------|-------------------|---------------------|-------------------------------------------------------------------------|
| 1      | 135.81            | **95.31%**          | {0: 92.46%, 1: 97.93%}                                                 |
| 2      | 420.31            | **97.84%**          | {0: 93.08%, 1: 96.62%, 2: 100.00%}                                     |
| 3      | 524.70            | **98.20%**          | {0: 91.04%, 1: 98.31%, 2: 100.00%, 3: 100.00%}                         |
| 4      | 661.33            | **96.91%**          | {0: 88.59%, 1: 98.68%, 2: 99.60%, 3: 100.00%, 4: 96.39%, 5: 97.86%}    |

### ✔️ DynEx-CLoRA (All Similarity Test, α = 0.1)

| Period | Training Time (s) | Validation Accuracy | Class-wise Accuracy                                                    |
|--------|-------------------|---------------------|-------------------------------------------------------------------------|
| 1      | 168.95            | **95.50%**          | {0: 92.87%, 1: 97.93%}                                                 |
| 2      | 487.90            | **97.93%**          | {0: 93.69%, 1: 96.43%, 2: 100.00%}                                     |
| 3      | 513.51            | **98.30%**          | {0: 93.69%, 1: 96.43%, 2: 100.00%, 3: 100.00%}                         |
| 4      | 599.29            | **97.49%**          | {0: 94.50%, 1: 95.30%, 2: 99.80%, 3: 100.00%, 4: 96.18%, 5: 99.29%}    |

### DynEx-CLoRA (All Similarity Test, α = 0.2)

| Period | Training Time (s) | Validation Accuracy | Class-wise Accuracy                                                    |
|--------|-------------------|---------------------|-------------------------------------------------------------------------|
| 1      | 149.07            | **95.31%**          | {0: 95.32%, 1: 95.30%}                                                 |
| 2      | 436.89            | **98.05%**          | {0: 92.87%, 1: 97.74%, 2: 100.00%}                                     |
| 3      | 609.50            | **98.24%**          | {0: 93.48%, 1: 96.24%, 2: 100.00%, 3: 100.00%}                         |
| 4      | 1537.80           | **96.54%**          | {0: 92.46%, 1: 96.05%, 2: 99.80%, 3: 100.00%, 4: 92.99%, 5: 97.62%}    |


---

## __Extra__

---
### Period 1 (alpha = 0.1, similarity_threshold = 0.5)
+ ##### Total training time: 168.95 seconds
+ ##### Model: HAR_MLP_LoRA_v2
+ ##### Training and saving in *'Class_Incremental_CL/HAR_CIL/Trained_models/DynEx_CLoRA/alpha_0.1_/sim_thd_0.5/Period_1'*
+ ##### Best Epoch: 219
#### __Val Accuracy: 95.50%__
#### __Val-Class-Acc: {0: '92.87%', 1: '97.93%'}__

In [17]:
# ================================
# 📌 Period 1 Configuration - HAR_MLP_LoRA_v2
# ================================
period = 1

# Load dataset for this period
X_train, y_train = period_datasets[period]["train"]
X_val, y_val     = period_datasets[period]["test"]

# Auto-select CUDA device
device = auto_select_cuda_device()

# Model and training hyperparameters
input_size    = X_train.shape[1]
hidden_size   = 128
output_size   = len(set(y_train))
dropout       = 0.2
learning_rate = 0.0001
weight_decay  = 1e-5
num_epochs    = 1000
alpha         = 0.1  # Not used in Period 1 but passed for compatibility
teacher_model = None
stable_classes = None

# Model saving path
model_name = "HAR_MLP_LoRA_v2"
model_saving_folder = os.path.join(
    "Class_Incremental_CL", "HAR_CIL", "Trained_models", 
    "DynEx_CLoRA", f"alpha_{alpha}_", f"sim_thd_{similarity_threshold}", f"Period_{period}"
)
os.makedirs(model_saving_folder, exist_ok=True)

# Initialize model, criterion, optimizer
student_model = HAR_MLP_LoRA_v2(
    input_size=input_size,
    hidden_size=hidden_size,
    output_size=output_size,
    dropout=dropout,
    lora_rank=4  # or whatever value you want
).to(device)

criterion = nn.CrossEntropyLoss()
optimizer = torch.optim.Adam(student_model.parameters(), lr=learning_rate, weight_decay=weight_decay)
scheduler = None

# Train the model
train_with_dynex_clora(
    model=student_model,
    teacher_model=teacher_model,
    output_size=output_size,
    criterion=criterion,
    optimizer=optimizer,
    X_train=X_train,
    y_train=y_train,
    X_val=X_val,
    y_val=y_val,
    num_epochs=num_epochs,
    batch_size=batch_size,
    alpha=alpha,
    model_saving_folder=model_saving_folder,
    model_name=model_name,
    stop_signal_file=stop_signal_file,
    scheduler=scheduler,
    period=period,
    stable_classes=stable_classes,
    class_features_dict=None,
    related_labels={"fc2": [0, 1]},  # Period 1 的初始化
    similarity_threshold=similarity_threshold
)

# ================================
# ✅ Summary & Resource Cleanup
# ================================
unique_classes = np.unique(y_train)
num_classes = len(unique_classes)

print(f"\n✅ Period {period} Training Complete. Final model architecture:")
print(student_model)
print(f"📊 Class Summary → unique_classes = {unique_classes}, num_classes = {num_classes}")

del X_train, y_train, X_val, y_val, teacher_model, student_model
gc.collect()
torch.cuda.empty_cache()


🎯 Automatically selected GPU:
    - CUDA Device ID : 0
    - Memory Used    : 20898 MiB
    - Device Name    : NVIDIA RTX A6000

🚀 'train_with_dynex_clora' started for Period 1

✅ Removed existing folder: Class_Incremental_CL/HAR_CIL/Trained_models/DynEx_CLoRA/alpha_0.1_/sim_thd_0.5/Period_1
🎯 Automatically selected GPU:
    - CUDA Device ID : 0
    - Memory Used    : 21165 MiB
    - Device Name    : NVIDIA RTX A6000

✅ Data Overview:
X_train: torch.Size([2660, 561]), y_train: torch.Size([2660])
X_val: torch.Size([1023, 561]), y_val: torch.Size([1023])

📐 Model Architecture:
HAR_MLP_LoRA_v2(
  (fc1): Linear(in_features=561, out_features=128, bias=True)
  (bn1): BatchNorm1d(128, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  (relu1): ReLU()
  (dropout1): Dropout(p=0.2, inplace=False)
  (fc2): Linear(in_features=128, out_features=128, bias=True)
  (lora_adapters): ModuleList()
  (bn2): BatchNorm1d(128, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  (

---
### Period 2 (alpha = 0.1, similarity_threshold = 0.5)
+ ##### Total training time: 487.90 seconds
+ ##### Model: HAR_MLP_LoRA_v2
+ ##### Training and saving in *'Class_Incremental_CL/HAR_CIL/Trained_models/DynEx_CLoRA/alpha_0.1_/sim_thd_0.5/Period_2'*
+ ##### Best Epoch: 774
#### __Val Accuracy: 97.93%__
#### __Val-Class-Acc: {0: '93.69%', 1: '96.43%', 2: '100.00%'}__

In [19]:
# ================================
# 📌 Period 2 Configuration - HAR_MLP_LoRA_v2
# ================================
period = 2

X_train, y_train = period_datasets[period]["train"]
X_val, y_val     = period_datasets[period]["test"]

device = auto_select_cuda_device()

input_size    = X_train.shape[1]
hidden_size   = 128
output_size   = len(set(y_train))
dropout       = 0.2
learning_rate = 0.0001
weight_decay  = 1e-5
num_epochs    = 1000
alpha         = 0.1
stable_classes = [0, 1]  # 根據 Period 1 類別定義

model_name = "HAR_MLP_LoRA_v2"
model_saving_folder = os.path.join(
    "Class_Incremental_CL", "HAR_CIL", "Trained_models", 
    "DynEx_CLoRA", f"alpha_{alpha}_", f"sim_thd_{similarity_threshold}", f"Period_{period}"
)
os.makedirs(model_saving_folder, exist_ok=True)

# Load previous class features
prev_folder = os.path.join(
    "Class_Incremental_CL", "HAR_CIL", "Trained_models", 
    "DynEx_CLoRA", f"alpha_{alpha}_", f"sim_thd_{similarity_threshold}", f"Period_{period - 1}"
)
class_features_path = os.path.join(prev_folder, "class_features.pkl")
if os.path.exists(class_features_path):
    with open(class_features_path, 'rb') as f:
        class_features_dict = pickle.load(f)
    print(f"✅ Loaded class features from: {class_features_path}")
else:
    class_features_dict = {}
    print("⚠️ No previous class features found.")

# Load previous model as teacher
teacher_checkpoint_path = os.path.join(prev_folder, f"{model_name}_best.pth")
teacher_model = HAR_MLP_LoRA_v2(
    input_size=input_size,
    hidden_size=hidden_size,
    output_size=output_size - 1,  # Exclude new class
    dropout=dropout,
    lora_rank=4
).to(device)

checkpoint = torch.load(teacher_checkpoint_path, map_location=device)
num_lora_adapters = checkpoint.get("num_lora_adapters", 0)
print(f"Teacher model num_lora_adapters: {num_lora_adapters}")
related_labels = checkpoint.get("related_labels", {"fc2": [0, 1]})
print(f"Teacher checkpoint has {num_lora_adapters} LoRA adapters.")

for _ in range(num_lora_adapters):
    teacher_model.add_lora_adapter()
teacher_model.load_state_dict(checkpoint["model_state_dict"])
del checkpoint

# Instantiate student and initialize from teacher (except fc3)
student_model = HAR_MLP_LoRA_v2(
    input_size=input_size,
    hidden_size=hidden_size,
    output_size=output_size,
    dropout=dropout,
    lora_rank=4
).to(device)

for _ in range(num_lora_adapters):
    student_model.add_lora_adapter()

# Copy shared weights
teacher_dict = teacher_model.state_dict()
student_dict = student_model.state_dict()
for name, param in teacher_dict.items():
    if not name.startswith("fc3"):
        student_dict[name].copy_(param)
student_model.load_state_dict(student_dict)

# Train setup
criterion = nn.CrossEntropyLoss()
optimizer = torch.optim.Adam(student_model.parameters(), lr=learning_rate, weight_decay=weight_decay)
scheduler = None

# Train
train_with_dynex_clora(
    model=student_model,
    teacher_model=teacher_model,
    output_size=output_size,
    criterion=criterion,
    optimizer=optimizer,
    X_train=X_train,
    y_train=y_train,
    X_val=X_val,
    y_val=y_val,
    num_epochs=num_epochs,
    batch_size=batch_size,
    alpha=alpha,
    model_saving_folder=model_saving_folder,
    model_name=model_name,
    stop_signal_file=stop_signal_file,
    scheduler=scheduler,
    period=period,
    stable_classes=stable_classes,
    class_features_dict=class_features_dict,
    related_labels=related_labels,
    logic_version="all",  # or "all"
    similarity_threshold=similarity_threshold
)

# Cleanup
unique_classes = np.unique(y_train)
print(f"\nstudent_model summary:\n{student_model}")
print(f"unique_classes = {unique_classes}, num_classes = {len(unique_classes)}")

del X_train, y_train, X_val, y_val, teacher_model, student_model, teacher_dict, student_dict, teacher_checkpoint_path
gc.collect()
torch.cuda.empty_cache()


🎯 Automatically selected GPU:
    - CUDA Device ID : 0
    - Memory Used    : 19915 MiB
    - Device Name    : NVIDIA RTX A6000
✅ Loaded class features from: Class_Incremental_CL/HAR_CIL/Trained_models/DynEx_CLoRA/alpha_0.1_/sim_thd_0.5/Period_1/class_features.pkl
Teacher model num_lora_adapters: 0
Teacher checkpoint has 0 LoRA adapters.

🚀 'train_with_dynex_clora' started for Period 2

✅ Removed existing folder: Class_Incremental_CL/HAR_CIL/Trained_models/DynEx_CLoRA/alpha_0.1_/sim_thd_0.5/Period_2
🎯 Automatically selected GPU:
    - CUDA Device ID : 0
    - Memory Used    : 19915 MiB
    - Device Name    : NVIDIA RTX A6000

✅ Data Overview:
X_train: torch.Size([5945, 561]), y_train: torch.Size([5945])
X_val: torch.Size([2410, 561]), y_val: torch.Size([2410])


/tmp/ipykernel_1055652/563750253.py:52: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  checkpoint = torch.load(teacher_checkpoint_path, map_location=device)



🔎 Similarity Scores:
New Class 0:
  - Existing Class 0: 0.4898
  - Existing Class 1: 0.4818
New Class 1:
  - Existing Class 0: 0.5446
  - Existing Class 1: 0.5575
New Class 2:
  - Existing Class 0: 0.4096
  - Existing Class 1: 0.4074
📊 Average similarity: 0.4818, Std: 0.0584
🧩 Similarity threshold: 0.5
👥 Existing classes: [0, 1]
🆕 New classes: [0, 1, 2]
🧩 New classes detected (for LoRA decision): [2]
✅ Added LoRA adapter to HAR_MLP_LoRA_v2 (fc2), total adapters: 1
[Stability Check] Class 0 similarity with itself: 0.4898
⚠️ Unfreezing fc2 due to low self-similarity of Class 0
[Stability Check] Class 1 similarity with itself: 0.5575

📌 related_labels (after logic): {'fc2': [0, 1], 0: [2]}
📌 to_unfreeze set: {'fc2'}
📌 new_lora_indices: [0]

📐 Model Architecture:
HAR_MLP_LoRA_v2(
  (fc1): Linear(in_features=561, out_features=128, bias=True)
  (bn1): BatchNorm1d(128, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  (relu1): ReLU()
  (dropout1): Dropout(p=0.2, inplace=False

---
### Period 3 (alpha = 0.1, similarity_threshold = 0.5)
+ ##### Total training time: 495.62 seconds
+ ##### Model: HAR_MLP_LoRA_v2
+ ##### Training and saving in *'Class_Incremental_CL/HAR_CIL/Trained_models/DynEx_CLoRA/alpha_0.1_/sim_thd_0.5/Period_3'*
+ ##### Best Epoch: 841
#### __Val Accuracy: 98.30%__
#### __Val-Class-Acc: {0: '94.30%', 1: '95.86%', 3: '100.00%', 2: '100.00%'}__

In [22]:
# ================================
# 📌 Period 3 Configuration - HAR_MLP_LoRA_v2
# ================================
period = 3

X_train, y_train = period_datasets[period]["train"]
X_val, y_val     = period_datasets[period]["test"]

input_size    = X_train.shape[1]
hidden_size   = 128
output_size   = len(set(y_train))
dropout       = 0.2
learning_rate = 0.0001
weight_decay  = 5e-6
num_epochs    = 1000
alpha         = 0.1
stable_classes = [0, 1, 2]

model_name = "HAR_MLP_LoRA_v2"
model_saving_folder = os.path.join(
    "Class_Incremental_CL", "HAR_CIL", "Trained_models", 
    "DynEx_CLoRA", f"alpha_{alpha}_", f"sim_thd_{similarity_threshold}", f"Period_{period}"
)
os.makedirs(model_saving_folder, exist_ok=True)

prev_folder = os.path.join(
    "Class_Incremental_CL", "HAR_CIL", "Trained_models", 
    "DynEx_CLoRA", f"alpha_{alpha}_", f"sim_thd_{similarity_threshold}", f"Period_{period - 1}"
)
class_features_path = os.path.join(prev_folder, "class_features.pkl")
if os.path.exists(class_features_path):
    with open(class_features_path, 'rb') as f:
        class_features_dict = pickle.load(f)
    print(f"✅ Loaded class features from: {class_features_path}")
else:
    class_features_dict = {}
    print("⚠️ No previous class features found.")

teacher_checkpoint_path = os.path.join(prev_folder, f"{model_name}_best.pth")
teacher_model = HAR_MLP_LoRA_v2(
    input_size=input_size,
    hidden_size=hidden_size,
    output_size=output_size - 1,
    dropout=dropout,
    lora_rank=4
).to(device)

checkpoint = torch.load(teacher_checkpoint_path, map_location=device)
num_lora_adapters = checkpoint.get("num_lora_adapters", 0)
related_labels = checkpoint.get("related_labels", {"fc2": [0, 1]})
for _ in range(num_lora_adapters):
    teacher_model.add_lora_adapter()
teacher_model.load_state_dict(checkpoint["model_state_dict"])
del checkpoint

student_model = HAR_MLP_LoRA_v2(
    input_size=input_size,
    hidden_size=hidden_size,
    output_size=output_size,
    dropout=dropout,
    lora_rank=4
).to(device)
for _ in range(num_lora_adapters):
    student_model.add_lora_adapter()

teacher_dict = teacher_model.state_dict()
student_dict = student_model.state_dict()
for name, param in teacher_dict.items():
    if not name.startswith("fc3"):
        student_dict[name].copy_(param)
student_model.load_state_dict(student_dict)

criterion = nn.CrossEntropyLoss()
optimizer = torch.optim.Adam(student_model.parameters(), lr=learning_rate, weight_decay=weight_decay)
scheduler = None

train_with_dynex_clora(
    model=student_model,
    teacher_model=teacher_model,
    output_size=output_size,
    criterion=criterion,
    optimizer=optimizer,
    X_train=X_train,
    y_train=y_train,
    X_val=X_val,
    y_val=y_val,
    num_epochs=num_epochs,
    batch_size=batch_size,
    alpha=alpha,
    model_saving_folder=model_saving_folder,
    model_name=model_name,
    stop_signal_file=stop_signal_file,
    scheduler=scheduler,
    period=period,
    stable_classes=stable_classes,
    class_features_dict=class_features_dict,
    related_labels=related_labels,
    logic_version="all",
    similarity_threshold=similarity_threshold
)

unique_classes = np.unique(y_train)
print(f"\nstudent_model summary:\n{student_model}")
print(f"unique_classes = {unique_classes}, num_classes = {len(unique_classes)}")

del X_train, y_train, X_val, y_val, teacher_model, student_model, teacher_dict, student_dict, teacher_checkpoint_path
gc.collect()
torch.cuda.empty_cache()


✅ Loaded class features from: Class_Incremental_CL/HAR_CIL/Trained_models/DynEx_CLoRA/alpha_0.1_/sim_thd_0.5/Period_2/class_features.pkl
✅ Added LoRA adapter to HAR_MLP_LoRA_v2 (fc2), total adapters: 1
✅ Added LoRA adapter to HAR_MLP_LoRA_v2 (fc2), total adapters: 1

🚀 'train_with_dynex_clora' started for Period 3

✅ Removed existing folder: Class_Incremental_CL/HAR_CIL/Trained_models/DynEx_CLoRA/alpha_0.1_/sim_thd_0.5/Period_3


/tmp/ipykernel_1055652/3021277226.py:48: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  checkpoint = torch.load(teacher_checkpoint_path, map_location=device)


🎯 Automatically selected GPU:
    - CUDA Device ID : 0
    - Memory Used    : 19917 MiB
    - Device Name    : NVIDIA RTX A6000

✅ Data Overview:
X_train: torch.Size([7352, 561]), y_train: torch.Size([7352])
X_val: torch.Size([2947, 561]), y_val: torch.Size([2947])

🔎 Similarity Scores:
New Class 0:
  - Existing Class 0: 0.8067
  - Existing Class 1: 0.4349
  - Existing Class 2: 0.3901
New Class 1:
  - Existing Class 0: 0.4411
  - Existing Class 1: 0.7450
  - Existing Class 2: 0.2086
New Class 2:
  - Existing Class 0: 0.7001
  - Existing Class 1: 0.7836
  - Existing Class 2: 0.6467
New Class 3:
  - Existing Class 0: 0.4963
  - Existing Class 1: 0.4063
  - Existing Class 2: 0.1980
📊 Average similarity: 0.5215, Std: 0.2031
🧩 Similarity threshold: 0.5
👥 Existing classes: [0, 1, 2]
🆕 New classes: [0, 1, 2, 3]
🧩 New classes detected (for LoRA decision): [3]
✅ Added LoRA adapter to HAR_MLP_LoRA_v2 (fc2), total adapters: 2
[Stability Check] Class 0 similarity with itself: 0.8067
[Stability Che

## 📊 Summary: 

### ✔️ HAR - DynEx-CLoRA

| Period | Training Time (s) | Validation Accuracy | Class-wise Accuracy                                                    |
|--------|-------------------|---------------------|-------------------------------------------------------------------------|
| 1      | 149.07            | **95.31%**          | {0: 95.32%, 1: 95.30%}                                                 |
| 2      | 487.90            | **97.93%**          | {0: 93.69%, 1: 96.43%, 2: 100.00%}                                     |
| 3      | 513.51            | **98.30%**          | {0: 93.69%, 1: 96.43%, 2: 100.00%, 3: 100.00%}                         |
| 4      | 599.29            | **97.49%**          | {0: 94.50%, 1: 95.30%, 2: 99.80%, 3: 100.00%, 4: 96.18%, 5: 99.29%}    |